# **DATA 698 Capstone Project**

Course: DATA 698  
Author: Kory Martin  
Professor: Jamiel H. Sheikh  
Spring 2024

#### **1. Setup**

In [507]:
import re
import os
import math
import requests
import re
import nltk
import boto3
import io

import pandas as pd
import datetime as dt
import numpy as np

from dotenv import load_dotenv
from joblib import dump, load
from bs4 import BeautifulSoup
from nltk.corpus import stopwords
from nltk.util import ngrams
from nltk.stem import WordNetLemmatizer

In [3]:
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import CategoricalNB
from sklearn.linear_model import LogisticRegression
from sklearn.neural_network import MLPClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, BaggingClassifier
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.feature_extraction.text import CountVectorizer,TfidfTransformer,TfidfVectorizer

In [4]:
nltk.download('stopwords')   
nltk.download('wordnet')

wordnet_lemmatizer = WordNetLemmatizer()
stop_words = set(stopwords.words('english'))

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/korymartin/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/korymartin/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [522]:
load_dotenv()

s3 = boto3.client(
    's3',
    aws_access_key_id = os.getenv('AWS_ACCESS_KEY_ID'),
    aws_secret_access_key = os.getenv('AWS_SECRET_ACCESS_KEY'),
    region_name = os.getenv('REGION_NAME')
)

In [521]:
my_bucket = os.getenv('S3_BUCKET')
response = s3.list_objects(Bucket= my_bucket)

In [525]:
response = s3.list_objects(Bucket= my_bucket, Prefix='clean_files/')

for item in response.get('Contents'):
    print(item['Key'])

clean_files/
clean_files/block_group_census_variables.csv
clean_files/block_group_census_variables.xlsx
clean_files/census_features.parquet.parquet
clean_files/census_features_total.parquet
clean_files/census_features_total.parquet.parquet
clean_files/census_rows_df.parquet
clean_files/combined_df_final.parquet
clean_files/demographic_percentages.parquet
clean_files/demographic_percentages.parquet.parquet
clean_files/model_training_data.parquet.parquet
clean_files/model_training_data_mini.parquet
clean_files/models/
clean_files/models/ab_classifier.joblib
clean_files/models/bag_classifier.joblib
clean_files/models/count_vectorizer.joblib
clean_files/models/knn_classifier.joblib
clean_files/models/lr_classifier.joblib
clean_files/models/nb_classifier.joblib
clean_files/models/nnet_classifier.joblib
clean_files/models/rf_classifier.joblib
clean_files/models/tf_vectorizer.joblib
clean_files/precinct_census_mapping.parquet
clean_files/precinct_census_mapping.parquet.parquet
clean_files/pre

#### **2. Pre-processing and Feature Engineering**

##### **2.1 Precinct Level Results**

This code takes the data pulled from the Los Angeles County registrar office (WEBSITE) that are stored in an S3 Bucket - https://data698-capstone-project.s3.us-west-2.amazonaws.com/raw_files/precinct_results/

Key Steps:
1. Repeat this process for multiple election results
2. Retrieve data for various ballot measures over time (50+)


Final Dataset:
- County
- Voter Precinct
- Year
- Ballot measure
- Yes vote count
- No vote count
- Total vote count
- pct_support
- pct_oppose
- decision

Code to collect the munipality data into a single data frame

In [7]:
response = s3.list_objects(Bucket= my_bucket)
files = response.get("Contents")

file_list = []
for file in files:
    key = file['Key']
    if re.search('STATE_MEASURE',key) != None:
        file_list.append(key)

temp_file = "tempfile.xls"


measures_list = []
voter_precinct = []
election_dates = []
master_df = pd.DataFrame()

keep_cols = [0,1,2,6,8,9]
new_col_names= ['municipality', 'precinct','serial','group','support','opposed']

for file in file_list:

    s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=file)
    
    samp_df = pd.read_excel(temp_file)
    measure_name = samp_df.iloc[0,0]

    election_date = samp_df.columns[2]
    measures_list.append(measure_name)
    election_dates.append(election_date)

    samp_df = samp_df.iloc[2:,keep_cols].copy()
    samp_df = samp_df.set_axis(new_col_names, axis='columns')
    

    samp_df['election_date'] = election_date
    samp_df['measure_name'] = measure_name
    master_df = pd.concat([master_df, samp_df],axis=0)


In [8]:
master_df.head()

municipality  precinct serial          group support opposed election_date  \
2        ACTON  0050001F   6001  POLLING PLACE       0       0    2018-11-06   
3        ACTON  0050001F   6001    VBM PORTION       0       0    2018-11-06   
4        ACTON  0050001F   6001          TOTAL       0       0    2018-11-06   
5        ACTON  0050002A   6002  POLLING PLACE       0       0    2018-11-06   
6        ACTON  0050002A   6002    VBM PORTION       0       0    2018-11-06   

       measure_name  
2  STATE MEASURE 10  
3  STATE MEASURE 10  
4  STATE MEASURE 10  
5  STATE MEASURE 10  
6  STATE MEASURE 10

In [9]:
precinct_info = master_df.loc[(master_df['group'] == 'TOTAL') & (master_df['support'] > 0) & ~(master_df['municipality'].str.contains('BALLOT'))].copy()
precinct_info['total_voters'] = precinct_info.apply(lambda x: x['support'] + x['opposed'], axis=1)

Number of different ballot initiatives that are included in the precinct results data file

In [10]:
len(precinct_info['measure_name'].unique())

39

Number of unique precincts that are included in the precinct resuls data file

In [11]:
len(precinct_info['precinct'].unique())

7661

Calculate the percent of voters who were in support or opposition of the ballot initiative

In [12]:
precinct_info['pct_support'] = precinct_info.apply(lambda x: x['support']/x['total_voters'],axis=1)
precinct_info['pct_opposed'] = precinct_info.apply(lambda x: x['opposed']/x['total_voters'],axis=1)

Create a categorical variable to classify if the precint was in support or opposed to the ballot measure

In [13]:
precinct_info['voter_choice'] = precinct_info.apply(lambda x: 'support' if x['pct_support'] > 0.5 else 'opposed', axis=1)

In [14]:
precinct_info.loc[:,['election_date','measure_name','precinct','voter_choice']].head()

election_date      measure_name  precinct voter_choice
13    2018-11-06  STATE MEASURE 10  0050003A      opposed
16    2018-11-06  STATE MEASURE 10  0050004B      opposed
19    2018-11-06  STATE MEASURE 10  0050005A      opposed
22    2018-11-06  STATE MEASURE 10  0050014A      opposed
25    2018-11-06  STATE MEASURE 10  0050022A      opposed

Create standard ID field that will be used to join this data with other newly created data tables

In [15]:
precinct_info['election_year'] = precinct_info.apply(lambda x: x['election_date'].year,axis=1)
precinct_info['prop_num'] = precinct_info.apply(lambda x: re.findall('\d{1,2}',x['measure_name'])[0],axis=1)
precinct_info['prop_code'] = precinct_info.apply(lambda x: "PROP"+'{:02d}'.format(int(x['prop_num']))+"_"+str(x['election_year']),axis=1)

In [16]:
precinct_info.head()

municipality  precinct serial  group support opposed election_date  \
13        ACTON  0050003A      1  TOTAL     143     612    2018-11-06   
16        ACTON  0050004B      2  TOTAL      62     360    2018-11-06   
19        ACTON  0050005A      3  TOTAL     110     411    2018-11-06   
22        ACTON  0050014A      4  TOTAL     101     318    2018-11-06   
25        ACTON  0050022A   6004  TOTAL      12      30    2018-11-06   

        measure_name  total_voters  pct_support  pct_opposed voter_choice  \
13  STATE MEASURE 10           755     0.189404     0.810596      opposed   
16  STATE MEASURE 10           422     0.146919     0.853081      opposed   
19  STATE MEASURE 10           521     0.211132     0.788868      opposed   
22  STATE MEASURE 10           419     0.241050     0.758950      opposed   
25  STATE MEASURE 10            42     0.285714     0.714286      opposed   

    election_year prop_num    prop_code  
13           2018       10  PROP10_2018  
16           2018       10  PROP10_2018  
19           2018       10  PROP10_2018  
22           2018       10  PROP10_2018  
25           2018       10  PROP10_2018

Create a simplified data table that has the precinct level voter choise for each state proposition

In [17]:
voter_selections = precinct_info.loc[:,['precinct','prop_code','voter_choice']].copy()
voter_selections = voter_selections.reset_index(drop=True)

In [18]:
voter_selections.head()

precinct    prop_code voter_choice
0  0050003A  PROP10_2018      opposed
1  0050004B  PROP10_2018      opposed
2  0050005A  PROP10_2018      opposed
3  0050014A  PROP10_2018      opposed
4  0050022A  PROP10_2018      opposed

In [19]:
##Upload Parquet File to S3

parquet_file = 'voter_selection.parquet'
voter_selections.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

In [20]:
del samp_df, master_df, precinct_info

##### **2.2 Text Corpus**

Ballot initiative text

This is focused on importing the data for the corpus representing the different ballot initiatives. 

Web Scraper for Data

Main sources:
1. [Secretary of State](https://vigarchive.sos.ca.gov/)
2. [Legislative Analysts' Office](https://lao.ca.gov/BallotAnalysis)
3. [UC San Francisco Law School](https://repository.uclawsf.edu/ca_ballot_props/)
4. [Wikipedia](https://en.wikipedia.org/wiki/List_of_California_ballot_propositions)
5. [League of Women Voters](https://cavotes.org/ballot-measures/)

The final dataframe should have the following structure:
- Source Name
- Source Link
- Election Year / Date
- Identifier (STATE MEASURE PROP_NUMBER)
- Measure Name
- Abstract / Summary Text

2.2.1 Voter Guide Archive

In [21]:
main_url = 'https://vigarchive.sos.ca.gov/'
data = requests.get(main_url)

html = BeautifulSoup(data.text,'html.parser')
main_content = html.find(id="mainCont")
li_tags = main_content.find('ul').find_all('li')

prop_info = []

for i in li_tags:
    href = i.find('a')['href']
    election_title = i.text
    new_url=main_url+href
    
    mini_dict={'new_url':new_url, 'election_title':election_title}
    prop_info.append(mini_dict)


In [22]:
prop_info

[{'new_url': 'https://vigarchive.sos.ca.gov/2024/primary/',
  'election_title': '2024 California Primary Election'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2022/general/',
  'election_title': '2022 California General Election'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2022/',
  'election_title': '2022 California Primary Election'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2021/',
  'election_title': '2021 California Recall Election'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2020/primary/',
  'election_title': '2020 California Primary Election'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2018/primary/',
  'election_title': '2018 California Primary Election'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2018/general/',
  'election_title': '2018 California General Election'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2016/general/',
  'election_title': '2016 California General Election'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2016/primary/',
  'election_title': '

In [23]:

prop_links = []

for prop in prop_info:

    url = prop['new_url']
    data = requests.get(url)
    new_html = BeautifulSoup(data.text,'html.parser')
    if new_html.find(id='mainNavCtnr'):
        main_nav = new_html.find_all(id="mainNavCtnr")
    else:
        main_nav = new_html.find_all(id="globalLinks")
    
    if main_nav:
        li_tags = main_nav[0].find_all('li')
        
        
        
        for li in li_tags:
            
            if li.text =='Propositions':
                href = li.find('a')['href']
                #prop_links.append(href)
                prop['prop_group_url'] = main_url[:-1]+href
                prop_links.append(prop)
                

In [24]:
prop_links

[{'new_url': 'https://vigarchive.sos.ca.gov/2024/primary/',
  'election_title': '2024 California Primary Election',
  'prop_group_url': 'https://vigarchive.sos.ca.gov/2024/primary/propositions/'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2022/general/',
  'election_title': '2022 California General Election',
  'prop_group_url': 'https://vigarchive.sos.ca.gov/2022/general/propositions/'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2020/primary/',
  'election_title': '2020 California Primary Election',
  'prop_group_url': 'https://vigarchive.sos.ca.gov/2020/primary/propositions/'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2018/primary/',
  'election_title': '2018 California Primary Election',
  'prop_group_url': 'https://vigarchive.sos.ca.gov/2018/primary/propositions/'},
 {'new_url': 'https://vigarchive.sos.ca.gov/2018/general/',
  'election_title': '2018 California General Election',
  'prop_group_url': 'https://vigarchive.sos.ca.gov/2018/general/propositions/'},
 {'new_url': 'h

In [25]:

new_prop_info = []

for item in prop_links:

    data = requests.get(item['prop_group_url'])
    html = BeautifulSoup(data.text,'html.parser')
    li_content = html.find('ol').find_all('li')[2].contents
    for i in li_content:
        result = re.findall('[\w]+.\d{1,2},.\d{4}',i.text)
        if len(result) > 0:
            election_date = result[0]
    if len(html.find_all(id='mainCont')) > 0:
        main_content = html.find_all(id='mainCont')[0]
    else:
        main_content = html.find_all(id='content')[0]
    prop_sub_links = main_content.find_all('ul')[0].find_all('li')


    for prop_item in prop_sub_links:
        new_url = main_url[:-1]+prop_item.find('a')['href']

        if len(re.findall('.gov\/[\d]{4}\/[\w]+', new_url)) > 0:
            mini_dict = {}
            title = prop_item.text

            mini_dict['prop_name'] = title
            mini_dict['election_date'] = election_date
            mini_dict['prop_url'] = new_url
            new_prop_info.append(mini_dict)

In [26]:

prop_details = []

for item in new_prop_info:


    data =requests.get(item['prop_url'])
    html = BeautifulSoup(data.text,'html.parser')
    if html.find_all('aside')[0].find(id='propSubpages'):
        href = html.find_all('aside')[0].find(id='propSubpages').find_all('li')[0].find('a')['href']
        new_url = main_url[:-1]+href
        data = requests.get(new_url)
        html = BeautifulSoup(data.text,'html.parser')
        if re.findall('.gov\/2012',item['prop_url']):
            top = html.find_all(id='content')
            prop_title = top[0].find_all('div')[2].find(class_='propName').text
            summary_text = top[0].find_all('ul')[1].find_all('li')

            for summary in summary_text:
                    mini_dict = {}
                    mini_dict['prop_title'] = prop_title
                    mini_dict['prop_name'] = item['prop_name']
                    mini_dict['election_date'] = item['election_date']
                    mini_dict['prop_summary'] = summary.text
                    prop_details.append(mini_dict)
        else:
            top = html.find_all(id='top')
            if len(top) > 0:
                prop_title = top[0].find_all(id='mainCont')[0].find_all('div')[2].find(class_='propName').text
                summary_text = top[0].find_all(id='mainCont')[0].find_all('ul')[1].find_all('li')

                for summary in summary_text:
                    mini_dict = {}
                    mini_dict['prop_title'] = prop_title
                    mini_dict['prop_name'] = item['prop_name']
                    mini_dict['election_date'] = item['election_date']
                    mini_dict['prop_summary'] = summary.text
                    prop_details.append(item)

    

In [27]:
df1 = pd.DataFrame(prop_details)

In [28]:
df1.head()
df1['source_url'] = main_url
df1['source'] = 'California Secretary of State'

2.2.2. Legislative Analyst's Office

In [29]:
prop_summary_df = []

main_url = 'https://lao.ca.gov/BallotAnalysis/Propositions?date=12%2F31%2F9999&propNumber=&searchTerm='
data = requests.get(main_url)
html = BeautifulSoup(data.text, 'html.parser')
container = html.find(class_='container')
prop_info = container.find(class_='row').find_all(class_='col-md-8')[0].find_all(class_='card')

for prop in prop_info:
    
    prop_name = prop.find(class_="card-title").text
    election_date = prop.find("small").text
    prop_desc = prop.find(class_="card-subtitle").text
    prop_summary = prop.find(class_="card-text").find_all('p')

    for i in range(1):
        mini_dict = {}
        mini_dict['election_date'] = election_date
        mini_dict['prop_name'] = prop_name
        mini_dict['prop_desc'] = prop_desc
        if len(prop_summary) > i:
            mini_dict['prop_summary'] = prop_summary[i].text
        else:
            mini_dict['prop_summary'] = ""
        prop_summary_df.append(mini_dict)
    

In [30]:
df2 = pd.DataFrame(prop_summary_df)

In [31]:
df2['source_url'] = 'https://lao.ca.gov/BallotAnalysis/'
df2['source'] = 'Legislative Analysts Office'

In [32]:
df2.head()

election_date       prop_name  \
0     March 5, 2024   Proposition 1   
1  November 8, 2022   Proposition 1   
2  November 8, 2022  Proposition 26   
3  November 8, 2022  Proposition 27   
4  November 8, 2022  Proposition 28   

                                           prop_desc  \
0  Authorizes $6.38 Billion in Bonds to Build Men...   
1  Constitutional Right to Reproductive Freedom. ...   
2  Allows In-Person Roulette, Dice Games, Sports ...   
3  Allows Online and Mobile Sports Wagering Outsi...   
4  Provides Additional Funding for Arts and Music...   

                                        prop_summary  \
0  A YES vote on this measure means: Counties wou...   
1  A YES vote on this measure means: The Californ...   
2  A YES vote on this measure means: Four racetra...   
3  A YES vote on this measure means: Licensed tri...   
4  A YES vote on this measure means: The state wo...   

                           source_url                       source  
0  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
1  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
2  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
3  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
4  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office

2.2.3. League of Women Voters

In [33]:
base_url = 'https://cavotes.org'
main_url = 'https://cavotes.org/ballot-measures/'
data = requests.get(main_url)
html = BeautifulSoup(data.text, 'html.parser')
li_tags = html.find_all('li')
slugs = []

for li in li_tags:
    a_tag = li.find('a',attrs={'href':True})
    if a_tag:
    
        href= a_tag['href']
        match_result = re.search('ballot-measure\/[\d]{4}',href)
        if match_result:
            #print(href)
            slugs.append(href)
prop_info = []

for slug in slugs:

    new_url = base_url+slug
    data = requests.get(new_url)
    html = BeautifulSoup(data.text,'html.parser')
    prop_num = html.find_all(class_='wp-block-details')[0].find_all('p')[0].contents[1].strip()
    prop_name =html.find_all(class_='wp-block-details')[0].find_all('p')[0].contents[4]
    #prop_election = html.find_all(class_='wp-block-details')[0].find_all('p')[0].contents[10].strip()
    html_content = html.find_all(class_='wp-block-details')[0].find_all('p')[0].contents
    #print(html_content)
    for i in html_content:    
        if len(re.findall('\d{4}.[\bGeneral\b|\bPrimary\b]+',i.text.strip())) > 0:
            prop_election = i.text.strip()
            #print(prop_election, new_url)
        else:
            #print(i.text, new_url)
            prop_election = None
    #print(prop_election, new_url,'\n\n')
    measure_question = list(html.find_all(class_='wp-block-heading')[1].next_siblings)[1].text

    li_tags = html.find_all(class_='entry-content')[0].find_all('ul')[0].find_all('li')
    for li in li_tags:
        mini_dict = {}
        mini_dict['prop_num'] = prop_num
        mini_dict['prop_name'] = prop_name
        mini_dict['prop_election'] = prop_election
        mini_dict['measure_question'] = measure_question
        mini_dict['summary_text'] = li.text
        prop_info.append(mini_dict)


In [34]:

df3 = pd.DataFrame(prop_info)

df3['source_url'] = 'https://cavotes.org'
df3['source'] = 'League of Women Voters'

In [35]:
df3.head()

prop_num                                          prop_name  \
0   Proposition 1      Constitutional Right To Reproductive Freedom    
1   Proposition 1      Constitutional Right To Reproductive Freedom    
2   Proposition 1      Constitutional Right To Reproductive Freedom    
3  Proposition 26  Allows In-Person Roulette, Dice Games, Sports ...   
4  Proposition 26  Allows In-Person Roulette, Dice Games, Sports ...   

  prop_election                                   measure_question  \
0  2022 General  Should the California Constitution expressly p...   
1  2022 General  Should the California Constitution expressly p...   
2  2022 General  Should the California Constitution expressly p...   
3  2022 General  Should California (a) increase the allowable g...   
4  2022 General  Should California (a) increase the allowable g...   

                                        summary_text           source_url  \
0  Prohibits the State from denying or interferin...  https://cavotes.org   
1  Specifies that this constitutional amendment i...  https://cavotes.org   
2  Specifies that nothing contained in the measur...  https://cavotes.org   
3  Allow tribal casinos to run roulette and dice ...  https://cavotes.org   
4  Allows tribal casinos and four-horse racetrack...  https://cavotes.org   

                   source  
0  League of Women Voters  
1  League of Women Voters  
2  League of Women Voters  
3  League of Women Voters  
4  League of Women Voters

2.2.4. Wikepedia

In [36]:
main_urls = ['https://en.wikipedia.org/wiki/List_of_California_ballot_propositions:_2010%E2%80%932019',\
             'https://en.wikipedia.org/wiki/List_of_California_ballot_propositions:_2020%E2%80%932029']

prop_info = []

data = requests.get(main_urls[0])
html = BeautifulSoup(data.text,'html.parser')

tables = html.find_all(class_='wikitable')

for table in tables: #html.find_all(class_='wikitable')[9].find_all('tr')[1:]
    tr = table.find_all('tr')[1:]

    for i in tr:
        if len(i.find_all(class_='mw-redirect')):
            mini_dict = {}
            prop_title = i.find('a')['title']
            prop_link = i.find('a')['href']
            prop_desc = i.find_all('td')[2].text
            mini_dict['prop_title'] = prop_title
            mini_dict['prop_link'] = prop_link
            mini_dict['prop_desc'] = prop_desc
            prop_info.append(mini_dict)
            #print(mini_dict)
            '''
            td = row.find_all('td')
            #print(td)
            if re.search('page does not exist',td[0].find('a')['title']) == None:
                
                print(mini_dict)
            '''


In [37]:

df4_a = pd.DataFrame(prop_info)
df4_a['source_url'] = 'https://en.wikipedia.org/wiki/List_of_California_ballot_propositions'
df4_a['source'] = 'Wikepedia'



In [38]:

prop_info = []

data = requests.get(main_urls[1])
html = BeautifulSoup(data.text,'html.parser')

tables = html.find_all(class_='wikitable')


for table in tables: #html.find_all(class_='wikitable')[9].find_all('tr')[1:]
    tr = table.find_all('tr')

    for i in tr:
        a_tag = i.find('a')
        #print(a_tag)
        if a_tag:
            mini_dict = {}
            prop_title = a_tag['title']
            prop_link = a_tag['href']
            prop_desc = i.find_all('td')[1].text
            mini_dict['prop_title'] = prop_title
            mini_dict['prop_link'] = prop_link
            mini_dict['prop_desc'] = prop_desc
            prop_info.append(mini_dict)
            #print(mini_dict)
            '''
            td = row.find_all('td')
            #print(td)
            if re.search('page does not exist',td[0].find('a')['title']) == None:
            
            print(mini_dict)
        '''


In [39]:

df4_b = pd.DataFrame(prop_info)
df4_b['source_url'] = 'https://en.wikipedia.org/wiki/List_of_California_ballot_propositions'
df4_b['source'] = 'Wikepedia'

In [40]:
df4 = pd.concat([df4_a, df4_b])

In [41]:
df4.head()

prop_title                               prop_link  \
0  California Proposition 13 (2010)  /wiki/California_Proposition_13_(2010)   
1  California Proposition 14 (2010)  /wiki/California_Proposition_14_(2010)   
2  California Proposition 15 (2010)  /wiki/California_Proposition_15_(2010)   
3  California Proposition 16 (2010)  /wiki/California_Proposition_16_(2010)   
4  California Proposition 17 (2010)  /wiki/California_Proposition_17_(2010)   

                                           prop_desc  \
0  Limits on property tax assessment. Seismic ret...   
1  Elections. Open primaries/"Top Two primary Act...   
2                   California Fair Elections Act.\n   
3  Imposes new two-thirds voter approval requirem...   
4  Allows auto insurance companies to base their ...   

                                          source_url     source  
0  https://en.wikipedia.org/wiki/List_of_Californ...  Wikepedia  
1  https://en.wikipedia.org/wiki/List_of_Californ...  Wikepedia  
2  https://en.wikipedia.org/wiki/List_of_Californ...  Wikepedia  
3  https://en.wikipedia.org/wiki/List_of_Californ...  Wikepedia  
4  https://en.wikipedia.org/wiki/List_of_Californ...  Wikepedia

2.2.5. UC Hastings




In [42]:
main_url = 'https://repository.uclawsf.edu/ca_ballot_props/'
data = requests.get(main_url)
html = BeautifulSoup(data.text,'html.parser')
articles = html.find_all(id='series-home')[0].select('.article-listing')


slugs = []

for article in articles:
    if article.select('.index_pubinfo'):
        prop_name = article.select('.index_pubinfo')[0].contents[1].text
        summary = article.find('a').text.title()
        href = article.find('a')['href']
        mini_dict = {}
        mini_dict['slug'] = href
        mini_dict['summary'] = summary
        mini_dict['prop_name'] = prop_name

        slugs.append(mini_dict)
prop_info = []

for slug in slugs:
    mini_dict ={}
    new_url = slug['slug']
    data = requests.get(new_url)
    html = BeautifulSoup(data.text,'html.parser')
    abstract = html.select('#abstract')[0].find('p').text.title()
    prop_num = html.select('#propnum')[0].find('p').text
    election_year = html.select('#publication_date')[0].find('p').text
    document_type = html.select('#document_type')[0].find('p').text
    election_type = html.select('#election_type')[0].find('p').text
    mini_dict['prop_num'] = prop_num
    mini_dict['election_year'] = election_year
    mini_dict['election_type'] = election_type
    mini_dict['abstract'] = abstract

    prop_info.append(mini_dict)


In [43]:

df5 = pd.DataFrame(prop_info)
df5['source_url'] = 'https://repository.uclawsf.edu/ca_ballot_props/'
df5['source'] = 'UC San Francisco'

In [44]:
df5.head()

prop_num election_year     election_type  \
0       16          2020  General Election   
1       18          2020  General Election   
2       24          2020  General Election   
3       13          2020           Primary   
4       14          2020  General Election   

                                            abstract  \
0  Permits Government Decision-Making Policies To...   
1  Fiscal Impact: Increased Statewide County Cost...   
2  Permits Consumers To: Prevent Businesses From ...   
3  Authorizes $15 Billion In State General Obliga...   
4  Authorizes $5.5 Billion State Bonds For: Stem ...   

                                        source_url            source  
0  https://repository.uclawsf.edu/ca_ballot_props/  UC San Francisco  
1  https://repository.uclawsf.edu/ca_ballot_props/  UC San Francisco  
2  https://repository.uclawsf.edu/ca_ballot_props/  UC San Francisco  
3  https://repository.uclawsf.edu/ca_ballot_props/  UC San Francisco  
4  https://repository.uclawsf.edu/ca_ballot_props/  UC San Francisco

Combined Text

Using the dataframes of the collected data from across the different data sources, I want to generate a singular data set that is common aongst the different groups. The final dataframe will contain the following:

- Source Name
- Source URL
- Election Date
- Prop Number
- Prop Summary

Secretary of State



In [45]:
df1.head()

prop_name  election_date  \
0  1 Authorizes $6.38 Billion in Bonds to Build M...  March 5, 2024   
1  1 Authorizes $6.38 Billion in Bonds to Build M...  March 5, 2024   
2  1 Authorizes $6.38 Billion in Bonds to Build M...  March 5, 2024   
3  1 Authorizes $6.38 Billion in Bonds to Build M...  March 5, 2024   
4  1 Authorizes $6.38 Billion in Bonds to Build M...  March 5, 2024   

                                            prop_url prop_title prop_summary  \
0  https://vigarchive.sos.ca.gov/2024/primary/pro...        NaN          NaN   
1  https://vigarchive.sos.ca.gov/2024/primary/pro...        NaN          NaN   
2  https://vigarchive.sos.ca.gov/2024/primary/pro...        NaN          NaN   
3  https://vigarchive.sos.ca.gov/2024/primary/pro...        NaN          NaN   
4  https://vigarchive.sos.ca.gov/2024/primary/pro...        NaN          NaN   

                       source_url                         source  
0  https://vigarchive.sos.ca.gov/  California Secretary of State  
1  https://vigarchive.sos.ca.gov/  California Secretary of State  
2  https://vigarchive.sos.ca.gov/  California Secretary of State  
3  https://vigarchive.sos.ca.gov/  California Secretary of State  
4  https://vigarchive.sos.ca.gov/  California Secretary of State

In [46]:
pd.DataFrame(df1.columns)

0
0      prop_name
1  election_date
2       prop_url
3     prop_title
4   prop_summary
5     source_url
6         source

In [47]:
keep_cols = [6,5,1,0,3,4]

In [48]:
df1_a = df1.iloc[:,keep_cols].copy()

In [49]:
df1_a.head()

source                      source_url  \
0  California Secretary of State  https://vigarchive.sos.ca.gov/   
1  California Secretary of State  https://vigarchive.sos.ca.gov/   
2  California Secretary of State  https://vigarchive.sos.ca.gov/   
3  California Secretary of State  https://vigarchive.sos.ca.gov/   
4  California Secretary of State  https://vigarchive.sos.ca.gov/   

   election_date                                          prop_name  \
0  March 5, 2024  1 Authorizes $6.38 Billion in Bonds to Build M...   
1  March 5, 2024  1 Authorizes $6.38 Billion in Bonds to Build M...   
2  March 5, 2024  1 Authorizes $6.38 Billion in Bonds to Build M...   
3  March 5, 2024  1 Authorizes $6.38 Billion in Bonds to Build M...   
4  March 5, 2024  1 Authorizes $6.38 Billion in Bonds to Build M...   

  prop_title prop_summary  
0        NaN          NaN  
1        NaN          NaN  
2        NaN          NaN  
3        NaN          NaN  
4        NaN          NaN

In [50]:
df1_a['prop_num'] = df1_a.apply(lambda x: re.findall('^\d{1,2}',x['prop_name'].strip())[0], axis=1)

In [51]:
pd.DataFrame(df1_a.columns)

0
0         source
1     source_url
2  election_date
3      prop_name
4     prop_title
5   prop_summary
6       prop_num

In [52]:
keep_cols = [0,1,2,6,5]

In [53]:
df1_b = df1_a.iloc[:,keep_cols].copy()

In [54]:
df1_b.head()

source                      source_url  \
0  California Secretary of State  https://vigarchive.sos.ca.gov/   
1  California Secretary of State  https://vigarchive.sos.ca.gov/   
2  California Secretary of State  https://vigarchive.sos.ca.gov/   
3  California Secretary of State  https://vigarchive.sos.ca.gov/   
4  California Secretary of State  https://vigarchive.sos.ca.gov/   

   election_date prop_num prop_summary  
0  March 5, 2024        1          NaN  
1  March 5, 2024        1          NaN  
2  March 5, 2024        1          NaN  
3  March 5, 2024        1          NaN  
4  March 5, 2024        1          NaN

Legislative Analysts Office

In [55]:
df2.head()

election_date       prop_name  \
0     March 5, 2024   Proposition 1   
1  November 8, 2022   Proposition 1   
2  November 8, 2022  Proposition 26   
3  November 8, 2022  Proposition 27   
4  November 8, 2022  Proposition 28   

                                           prop_desc  \
0  Authorizes $6.38 Billion in Bonds to Build Men...   
1  Constitutional Right to Reproductive Freedom. ...   
2  Allows In-Person Roulette, Dice Games, Sports ...   
3  Allows Online and Mobile Sports Wagering Outsi...   
4  Provides Additional Funding for Arts and Music...   

                                        prop_summary  \
0  A YES vote on this measure means: Counties wou...   
1  A YES vote on this measure means: The Californ...   
2  A YES vote on this measure means: Four racetra...   
3  A YES vote on this measure means: Licensed tri...   
4  A YES vote on this measure means: The state wo...   

                           source_url                       source  
0  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
1  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
2  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
3  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
4  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office

In [56]:
pd.DataFrame(df2.columns)

0
0  election_date
1      prop_name
2      prop_desc
3   prop_summary
4     source_url
5         source

In [57]:
keep_cols = [5,4,0,1,3]

In [58]:
df2.head()

election_date       prop_name  \
0     March 5, 2024   Proposition 1   
1  November 8, 2022   Proposition 1   
2  November 8, 2022  Proposition 26   
3  November 8, 2022  Proposition 27   
4  November 8, 2022  Proposition 28   

                                           prop_desc  \
0  Authorizes $6.38 Billion in Bonds to Build Men...   
1  Constitutional Right to Reproductive Freedom. ...   
2  Allows In-Person Roulette, Dice Games, Sports ...   
3  Allows Online and Mobile Sports Wagering Outsi...   
4  Provides Additional Funding for Arts and Music...   

                                        prop_summary  \
0  A YES vote on this measure means: Counties wou...   
1  A YES vote on this measure means: The Californ...   
2  A YES vote on this measure means: Four racetra...   
3  A YES vote on this measure means: Licensed tri...   
4  A YES vote on this measure means: The state wo...   

                           source_url                       source  
0  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
1  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
2  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
3  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office  
4  https://lao.ca.gov/BallotAnalysis/  Legislative Analysts Office

In [59]:
df2_a = df2.iloc[:,keep_cols].copy()

In [60]:
df2_a['prop_num'] = df2_a.apply(lambda x: re.findall('\d{1,3}',x['prop_name'])[0], axis=1)

In [61]:
df2_a

source                          source_url  \
0    Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
1    Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
2    Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
3    Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
4    Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
..                           ...                                 ...   
251  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
252  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
253  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
254  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
255  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   

        election_date        prop_name  \
0       March 5, 2024    Proposition 1   
1    November 8, 2022    Proposition 1   
2    November 8, 2022   Proposition 26   
3    November 8, 2022   Proposition 27   
4    November 8, 2022   Proposition 28   
..                ...              ...   
251    March 26, 1996  Proposition 199   
252    March 26, 1996  Proposition 200   
253    March 26, 1996  Proposition 201   
254    March 26, 1996  Proposition 202   
255    March 26, 1996  Proposition 203   

                                          prop_summary prop_num  
0    A YES vote on this measure means: Counties wou...        1  
1    A YES vote on this measure means: The Californ...        1  
2    A YES vote on this measure means: Four racetra...       26  
3    A YES vote on this measure means: Licensed tri...       27  
4    A YES vote on this measure means: The state wo...       28  
..                                                 ...      ...  
251                                                         199  
252                                                         200  
253                                                         201  
254                                                         202  
255                                                         203  

[256 rows x 6 columns]

In [62]:
df2_b = df2_a.iloc[:,[0,1,2,5,4]].copy()

In [63]:
df2_b['election_date'].unique()

array(['March 5, 2024', 'November 8, 2022', 'November 3, 2020',
       'March 3, 2020', 'November 6, 2018', 'June 5, 2018',
       'November 8, 2016', 'June 7, 2016', 'November 4, 2014',
       'June 3, 2014', 'November 6, 2012', 'June 5, 2012',
       'November 2, 2010', 'June 8, 2010', 'May 19, 2009',
       'November 4, 2008', 'June 3, 2008', 'February 5, 2008',
       'November 7, 2006', 'June 6, 2006', 'November 8, 2005',
       'November 2, 2004', 'March 2, 2004', 'October 7, 2003',
       'November 5, 2002', 'March 5, 2002', 'November 7, 2000',
       'March 7, 2000', 'November 3, 1998', 'June 2, 1998',
       'November 5, 1996', 'March 26, 1996'], dtype=object)

In [64]:
df2_b.head()

source                          source_url  \
0  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
1  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
2  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
3  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
4  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   

      election_date prop_num  \
0     March 5, 2024        1   
1  November 8, 2022        1   
2  November 8, 2022       26   
3  November 8, 2022       27   
4  November 8, 2022       28   

                                        prop_summary  
0  A YES vote on this measure means: Counties wou...  
1  A YES vote on this measure means: The Californ...  
2  A YES vote on this measure means: Four racetra...  
3  A YES vote on this measure means: Licensed tri...  
4  A YES vote on this measure means: The state wo...

League of Women Voters

In [65]:
df3.head()

prop_num                                          prop_name  \
0   Proposition 1      Constitutional Right To Reproductive Freedom    
1   Proposition 1      Constitutional Right To Reproductive Freedom    
2   Proposition 1      Constitutional Right To Reproductive Freedom    
3  Proposition 26  Allows In-Person Roulette, Dice Games, Sports ...   
4  Proposition 26  Allows In-Person Roulette, Dice Games, Sports ...   

  prop_election                                   measure_question  \
0  2022 General  Should the California Constitution expressly p...   
1  2022 General  Should the California Constitution expressly p...   
2  2022 General  Should the California Constitution expressly p...   
3  2022 General  Should California (a) increase the allowable g...   
4  2022 General  Should California (a) increase the allowable g...   

                                        summary_text           source_url  \
0  Prohibits the State from denying or interferin...  https://cavotes.org   
1  Specifies that this constitutional amendment i...  https://cavotes.org   
2  Specifies that nothing contained in the measur...  https://cavotes.org   
3  Allow tribal casinos to run roulette and dice ...  https://cavotes.org   
4  Allows tribal casinos and four-horse racetrack...  https://cavotes.org   

                   source  
0  League of Women Voters  
1  League of Women Voters  
2  League of Women Voters  
3  League of Women Voters  
4  League of Women Voters

In [66]:
df3_a = df3.iloc[:,[6,5,2,0,4]].copy()

In [67]:
df3_a['prop_num'] = df3_a.apply(lambda x: re.findall('\d{1,3}',x['prop_num'])[0], axis=1)

In [68]:
df3_a.head()

source           source_url prop_election prop_num  \
0  League of Women Voters  https://cavotes.org  2022 General        1   
1  League of Women Voters  https://cavotes.org  2022 General        1   
2  League of Women Voters  https://cavotes.org  2022 General        1   
3  League of Women Voters  https://cavotes.org  2022 General       26   
4  League of Women Voters  https://cavotes.org  2022 General       26   

                                        summary_text  
0  Prohibits the State from denying or interferin...  
1  Specifies that this constitutional amendment i...  
2  Specifies that nothing contained in the measur...  
3  Allow tribal casinos to run roulette and dice ...  
4  Allows tribal casinos and four-horse racetrack...

Wikipedia

In [69]:
df4.head()

prop_title                               prop_link  \
0  California Proposition 13 (2010)  /wiki/California_Proposition_13_(2010)   
1  California Proposition 14 (2010)  /wiki/California_Proposition_14_(2010)   
2  California Proposition 15 (2010)  /wiki/California_Proposition_15_(2010)   
3  California Proposition 16 (2010)  /wiki/California_Proposition_16_(2010)   
4  California Proposition 17 (2010)  /wiki/California_Proposition_17_(2010)   

                                           prop_desc  \
0  Limits on property tax assessment. Seismic ret...   
1  Elections. Open primaries/"Top Two primary Act...   
2                   California Fair Elections Act.\n   
3  Imposes new two-thirds voter approval requirem...   
4  Allows auto insurance companies to base their ...   

                                          source_url     source  
0  https://en.wikipedia.org/wiki/List_of_Californ...  Wikepedia  
1  https://en.wikipedia.org/wiki/List_of_Californ...  Wikepedia  
2  https://en.wikipedia.org/wiki/List_of_Californ...  Wikepedia  
3  https://en.wikipedia.org/wiki/List_of_Californ...  Wikepedia  
4  https://en.wikipedia.org/wiki/List_of_Californ...  Wikepedia

In [70]:
df4_a = df4.iloc[:,[4,3,0,2]].copy()

In [71]:
df4_a.head()

source                                         source_url  \
0  Wikepedia  https://en.wikipedia.org/wiki/List_of_Californ...   
1  Wikepedia  https://en.wikipedia.org/wiki/List_of_Californ...   
2  Wikepedia  https://en.wikipedia.org/wiki/List_of_Californ...   
3  Wikepedia  https://en.wikipedia.org/wiki/List_of_Californ...   
4  Wikepedia  https://en.wikipedia.org/wiki/List_of_Californ...   

                         prop_title  \
0  California Proposition 13 (2010)   
1  California Proposition 14 (2010)   
2  California Proposition 15 (2010)   
3  California Proposition 16 (2010)   
4  California Proposition 17 (2010)   

                                           prop_desc  
0  Limits on property tax assessment. Seismic ret...  
1  Elections. Open primaries/"Top Two primary Act...  
2                   California Fair Elections Act.\n  
3  Imposes new two-thirds voter approval requirem...  
4  Allows auto insurance companies to base their ...

In [72]:
df4_a['election_date'] = df4_a.apply(lambda x: re.findall('\d{4}',x['prop_title'])[0],axis=1)

In [73]:
df4_a['prop_num'] = df4_a.apply(lambda x: re.findall('\w+.\w+.\d{1,2}',x['prop_title'])[0],axis=1)

In [74]:
df4_a['prop_num'] = df4_a.apply(lambda x: re.findall('\d{1,2}',x['prop_num'])[0],axis=1)

In [75]:
df4_b = df4_a.iloc[:,[0,1,4,5,3]].copy()

In [76]:
df4_b.head()

source                                         source_url election_date  \
0  Wikepedia  https://en.wikipedia.org/wiki/List_of_Californ...          2010   
1  Wikepedia  https://en.wikipedia.org/wiki/List_of_Californ...          2010   
2  Wikepedia  https://en.wikipedia.org/wiki/List_of_Californ...          2010   
3  Wikepedia  https://en.wikipedia.org/wiki/List_of_Californ...          2010   
4  Wikepedia  https://en.wikipedia.org/wiki/List_of_Californ...          2010   

  prop_num                                          prop_desc  
0       13  Limits on property tax assessment. Seismic ret...  
1       14  Elections. Open primaries/"Top Two primary Act...  
2       15                   California Fair Elections Act.\n  
3       16  Imposes new two-thirds voter approval requirem...  
4       17  Allows auto insurance companies to base their ...

UC Hastings

In [77]:
df5.head()

prop_num election_year     election_type  \
0       16          2020  General Election   
1       18          2020  General Election   
2       24          2020  General Election   
3       13          2020           Primary   
4       14          2020  General Election   

                                            abstract  \
0  Permits Government Decision-Making Policies To...   
1  Fiscal Impact: Increased Statewide County Cost...   
2  Permits Consumers To: Prevent Businesses From ...   
3  Authorizes $15 Billion In State General Obliga...   
4  Authorizes $5.5 Billion State Bonds For: Stem ...   

                                        source_url            source  
0  https://repository.uclawsf.edu/ca_ballot_props/  UC San Francisco  
1  https://repository.uclawsf.edu/ca_ballot_props/  UC San Francisco  
2  https://repository.uclawsf.edu/ca_ballot_props/  UC San Francisco  
3  https://repository.uclawsf.edu/ca_ballot_props/  UC San Francisco  
4  https://repository.uclawsf.edu/ca_ballot_props/  UC San Francisco

In [78]:
df5_a = df5.iloc[:,[5,4,1,0,3]].copy()

In [79]:
df5_a.head()

source                                       source_url  \
0  UC San Francisco  https://repository.uclawsf.edu/ca_ballot_props/   
1  UC San Francisco  https://repository.uclawsf.edu/ca_ballot_props/   
2  UC San Francisco  https://repository.uclawsf.edu/ca_ballot_props/   
3  UC San Francisco  https://repository.uclawsf.edu/ca_ballot_props/   
4  UC San Francisco  https://repository.uclawsf.edu/ca_ballot_props/   

  election_year prop_num                                           abstract  
0          2020       16  Permits Government Decision-Making Policies To...  
1          2020       18  Fiscal Impact: Increased Statewide County Cost...  
2          2020       24  Permits Consumers To: Prevent Businesses From ...  
3          2020       13  Authorizes $15 Billion In State General Obliga...  
4          2020       14  Authorizes $5.5 Billion State Bonds For: Stem ...

Clean up dataframes for concatenation

In [80]:
df1_b.head()

source                      source_url  \
0  California Secretary of State  https://vigarchive.sos.ca.gov/   
1  California Secretary of State  https://vigarchive.sos.ca.gov/   
2  California Secretary of State  https://vigarchive.sos.ca.gov/   
3  California Secretary of State  https://vigarchive.sos.ca.gov/   
4  California Secretary of State  https://vigarchive.sos.ca.gov/   

   election_date prop_num prop_summary  
0  March 5, 2024        1          NaN  
1  March 5, 2024        1          NaN  
2  March 5, 2024        1          NaN  
3  March 5, 2024        1          NaN  
4  March 5, 2024        1          NaN

In [81]:
df2_b.head()

source                          source_url  \
0  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
1  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
2  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
3  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
4  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   

      election_date prop_num  \
0     March 5, 2024        1   
1  November 8, 2022        1   
2  November 8, 2022       26   
3  November 8, 2022       27   
4  November 8, 2022       28   

                                        prop_summary  
0  A YES vote on this measure means: Counties wou...  
1  A YES vote on this measure means: The Californ...  
2  A YES vote on this measure means: Four racetra...  
3  A YES vote on this measure means: Licensed tri...  
4  A YES vote on this measure means: The state wo...

In [82]:
df3_a.head()
df3_a.rename(columns={'prop_election':'election_date','summary_text':'prop_summary'},inplace=True)

In [83]:
df4_b.head()
df4_b.rename(columns={'prop_desc':'prop_summary'},inplace=True)

In [84]:
df5_a.head()
df5_a.rename(columns={'election_year':'election_date','abstract':'prop_summary'},inplace=True)

In [85]:
combined_df = pd.concat([df1_b, df2_b, df3_a, df4_b, df5_a])

In [86]:
combined_df_clean = combined_df.loc[combined_df['election_date'].notnull()].copy()

In [87]:
combined_df_clean['election_year'] = combined_df_clean.apply(lambda x: re.findall('\d{4}',x['election_date'])[0],axis=1)

In [88]:
combined_df_clean['election_year'] = combined_df_clean['election_year'].apply(lambda x: int(x))

In [89]:
combined_df_a = combined_df_clean.loc[combined_df_clean['election_year'] >= 2014].copy()

In [90]:
combined_df_a['doc_name'] = combined_df_a.apply(lambda x: "PROP"+'{:02d}'.format(int(x['prop_num']))+"_"+str(x['election_year']),axis=1)

In [91]:
combined_df_a.columns

Index(['source', 'source_url', 'election_date', 'prop_num', 'prop_summary',
       'election_year', 'doc_name'],
      dtype='object')

In [92]:
combined_df_a['prop_num'] = combined_df_a.apply(lambda x: '{:02d}'.format(int(x['prop_num'])),axis=1)

In [93]:
combined_df_a.head()

source                      source_url  \
0  California Secretary of State  https://vigarchive.sos.ca.gov/   
1  California Secretary of State  https://vigarchive.sos.ca.gov/   
2  California Secretary of State  https://vigarchive.sos.ca.gov/   
3  California Secretary of State  https://vigarchive.sos.ca.gov/   
4  California Secretary of State  https://vigarchive.sos.ca.gov/   

   election_date prop_num prop_summary  election_year     doc_name  
0  March 5, 2024       01          NaN           2024  PROP01_2024  
1  March 5, 2024       01          NaN           2024  PROP01_2024  
2  March 5, 2024       01          NaN           2024  PROP01_2024  
3  March 5, 2024       01          NaN           2024  PROP01_2024  
4  March 5, 2024       01          NaN           2024  PROP01_2024

In [94]:
combined_df_b = combined_df_a.iloc[:,[0,1,5,6,4,3]].copy()

In [95]:
combined_df_final = combined_df_b.loc[combined_df_b['prop_summary'].notnull()].reset_index(drop=True).copy()

Total number of documents inc corpus

In [96]:
len(combined_df_final)

317

In [97]:
combined_df_final.head()

source                          source_url  \
0  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
1  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
2  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
3  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   
4  Legislative Analysts Office  https://lao.ca.gov/BallotAnalysis/   

   election_year     doc_name  \
0           2024  PROP01_2024   
1           2022  PROP01_2022   
2           2022  PROP26_2022   
3           2022  PROP27_2022   
4           2022  PROP28_2022   

                                        prop_summary prop_num  
0  A YES vote on this measure means: Counties wou...       01  
1  A YES vote on this measure means: The Californ...       01  
2  A YES vote on this measure means: Four racetra...       26  
3  A YES vote on this measure means: Licensed tri...       27  
4  A YES vote on this measure means: The state wo...       28

In [98]:
#Upload parquet file to S3

parquet_file = 'combined_df_final.parquet'
combined_df_final.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

In [99]:
del combined_df, combined_df_a, combined_df_b, combined_df_clean, combined_df_final

In [100]:
del df1, df2, df3, df4, df5, df1_a,df1_b,df4_b,df5_a


In [101]:
del df2_a, df2_b, df3_a, df4_a

##### **2.3 Census Data**

In [102]:
data =requests.get('https://api.census.gov/data/2022/acs/acs5/variables.html')
html = BeautifulSoup(data.text,'html.parser')
table = html.find_all('table')
rows = table[0].find_all('tr')
col_labels = [item.text for item in rows[0].find_all('th')]

In [103]:
row_data = []

for i in range(2,len(rows)):
    td = rows[i].find_all('td')
    mini_dict = {}
    for j in range(len(col_labels)):
        mini_dict[col_labels[j]] = td[j].text.strip()
    row_data.append(mini_dict)
    #print(mini_dict)


In [104]:
census_rows_df = pd.DataFrame(row_data)

In [105]:
response = s3.list_objects(Bucket= my_bucket, Prefix='clean_files/block_group_census_variables.csv')
files = response.get("Contents")


temp_file = "tempfile.xls"
s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=files[0]['Key'])
census_variables = pd.read_csv(temp_file)

In [106]:
census_variables.head(10)

American Community Survey
0                                   B01001Sex by Age
1         2022: ACS 5-Year Estimates Detailed Tables
2                          American Community Survey
3                            B01002Median Age by Sex
4         2022: ACS 5-Year Estimates Detailed Tables
5                          American Community Survey
6             B01002AMedian Age by Sex (White Alone)
7         2022: ACS 5-Year Estimates Detailed Tables
8                          American Community Survey
9  B01002BMedian Age by Sex (Black or African Ame...

In [107]:
#Upload parquet file to S3

parquet_file = 'census_rows_df.parquet'
census_rows_df.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

In [108]:
available_codes = []

for i in range(0,len(census_variables),3):
    census_code = census_variables.iloc[i,0]
    code6 = census_code[:6]
    code7 = census_code[:7]
    label6 = census_code[6:]
    label7 = census_code[7:]

    if len(re.findall('^[A-Z]{2}', label6))>0:
        code = code7
        label = label7
    else:
        code = code6
        label = label6

    mini_dict = {'code':code, 'description':label}
    available_codes.append(mini_dict)

In [109]:
available_codes_df = pd.DataFrame(available_codes)

In [110]:
available_codes_df.head()

code                                        description
0   B01001                                         Sex by Age
1   B01002                                  Median Age by Sex
2  B01002A                    Median Age by Sex (White Alone)
3  B01002B  Median Age by Sex (Black or African American A...
4  B01002C  Median Age by Sex (American Indian and Alaska ...

ACS 5 Variables available for Block Groups

In [111]:
available_groups_df = census_rows_df[census_rows_df['Group'].isin(available_codes_df['code'].unique().tolist())].copy()

In [112]:
available_codes_list = available_codes_df['code'].tolist()

Index for the desired demographic fields:

- 0: Sex by Age
- 19: Hispanic or Latino Origin by Race
- 70: Sex by Marital Status for the Population 15 Years and Over
- 84: Educational Attainment for the Population 25 Years and Over
- 93: Household Income in the Past 12 Months (in 2022 Inflation-Adjusted Dollars)
- 167: Employment Status for the Population 16 Years and Over
- 172: Occupancy Status
- 173: Tenure
- 288: Types of Health Insurance Coverage by Age
- 291: Presence of a Computer and Type of Internet Subscription in Household

In [113]:
category_index = [0,19,70,84,93,167,172,173,288,291]

In [114]:
census_concepts_df = pd.DataFrame(available_groups_df['Concept'].unique()).rename(columns={0:'Category'})

In [115]:
category_names = [census_concepts_df.iloc[i,0] for i in category_index]

In [116]:
category_names

['Sex by Age',
 'Hispanic or Latino Origin by Race',
 'Sex by Marital Status for the Population 15 Years and Over',
 'Educational Attainment for the Population 25 Years and Over',
 'Household Income in the Past 12 Months (in 2022 Inflation-Adjusted Dollars)',
 'Employment Status for the Population 16 Years and Over',
 'Occupancy Status',
 'Tenure',
 'Types of Health Insurance Coverage by Age',
 'Presence of a Computer and Type of Internet Subscription in Household']

In [117]:
for i in range(len(category_index)):
    category = category_names[i]
    category_df = census_rows_df[census_rows_df['Concept'] == category]
    category_df_key = category_df.loc[:,['Name','Label']]
    if category == 'Types of Health Insurance Coverage by Age':
        
        category_ids = ['B27010_002E','B27010_003E','B27010_010E','B27010_017E','B27010_018E','B27010_019E','B27010_026E','B27010_033E','B27010_034E','B27010_035E','B27010_042E','B27010_050E','B27010_051E','B27010_052E','B27010_058E','B27010_066E']
        #category_ids = category_df_key[category_df_key['Name'].isin(select_ids)].unique().tolist()
        
    else:
    
        category_ids = category_df_key['Name'].unique().tolist()
    
    category_string = ",".join(category_ids)

    start_string = 'https://api.census.gov/data/2022/acs/acs5?'
    get_string = 'get=NAME,'+category_string+'&'
    for_string = 'for=block%20group:*&in=state:06&in=county:037&in=tract:*&'
    key_string = 'key=c2d234d2615efa3747adcbfaea41dd77e417b6d2'
    combined_string=start_string+get_string+for_string+key_string
    combined_string
    r = requests.get(combined_string)
    
    if r.status_code == 200:

        results = r.json()
        results_df = pd.DataFrame(results)
        
        #num_cols = len(results_df.columns)
        #if results_df.iloc[1:,1:(num_cols-4)].sum().sum() != 0:
        #results_df.fillna(0,inplace=True)
        
        parquet_file = 'census_df{:02d}'.format(i+1)
        results_df.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
        s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='raw_files/census_data/'+parquet_file+'.parquet')

        

**D. Voter profile information**

I need to figure out how to map voter precincts to census blocks, so that I can use the demographic information from census data to then derive a profile of the different voter precincts.

Some of the key demographic information I want to be able to determine:
- Race
- Income
- Home ownership
- Gender
- Party affiliation
- Education levels



**Methodology**

Now that we have the individual dataframes for each of the different census demographic data, we need to create mini tables that can be combined with our overall mapping data that will then be used to create a unified dataframe for our precinct demographic data.

The key steps are:
1. Create a list of the column names for our census identifier data
2. Import the parquet file 
3. Pull the census codes that are used in the dataframe
4. Evaluate the codes and determine which ones to keep
5. Create list of the codes that we want to keep
6. Append the identifier column names to this new list
7. Generate a modified df with only these columns
8. Create a simplified data frame that totals the values based on the census tract
9. This dataframe will be used as the dataframe that will be combined with the voter precinct info

**Code for creating demo dataframes**

In [118]:
def get_census_codes(data_file, census_df):
    temp_file = "tempfile.parquet"
    s3.download_file(Filename=temp_file, Bucket=my_bucket, Key='raw_files/census_data/'+data_file)
    #census_variables = pd.read_csv(temp_file)
    demo_df = pd.read_parquet(temp_file)
    col_names = demo_df.iloc[0].tolist()
    col_length = len(col_names)
    census_codes = col_names[1:col_length-4]
    #census_df[census_df['Name'].isin(census_codes)]
    #keep_col_names = census_df[census_df['Name'].isin(census_codes)].reset_index(drop=True).iloc[:12]['Name'].unique().tolist()
    col_mapping = census_df[census_df['Name'].isin(census_codes)].loc[:,['Name','Label']].reset_index(drop=True)

    return col_mapping, demo_df

In [119]:
def create_simplified_df(col_mapping, keep_index, demo_df, census_df):
    keep_col_names = col_mapping.iloc[keep_index]['Name'].tolist()
    keep_col_mapping = col_mapping[col_mapping['Name'].isin(keep_col_names)].loc[:,['Name','Label']].reset_index(drop=True)
    keep_col_name_mapping = [{keep_col_mapping.loc[i,'Name']:keep_col_mapping.loc[i,'Label']} for i in range(len(keep_col_mapping))]


    data_identifiers = ['state', 'county','tract','block group']
    keep_col_names = keep_col_names + data_identifiers
    
    col_names = demo_df.iloc[0].tolist()
    col_length = len(col_names)

    new_col_index = demo_df.iloc[0][demo_df.iloc[0].isin(keep_col_names)].index.tolist()
    demo_df_mod = demo_df.iloc[:,new_col_index]#[demo_df.iloc[:,new_col_index][1] != '0']
    
    

    new_cols = demo_df_mod.iloc[0].tolist()

    #print(new_cols)
    demo_df_mod = demo_df_mod.set_axis(new_cols,axis='columns').iloc[1:].copy()

    
    for item in keep_col_name_mapping:
        demo_df_mod.rename(columns=item,inplace=True)

    return demo_df_mod


**Gender**



In [120]:
census_codes_all, demo_df1 = get_census_codes('census_df01.parquet',census_rows_df)
demo_df1
keep_index = [1,25]
census_codes_all.iloc[keep_index]
df1_mod = create_simplified_df(census_codes_all,keep_index,demo_df1, census_rows_df)
df1_mod.head()

Estimate!!Total:!!Male: Estimate!!Total:!!Female: state county   tract  \
1                     677                       738    06    037  101110   
2                     884                       942    06    037  101110   
3                     344                       429    06    037  101110   
4                    1358                      1396    06    037  101122   
5                     740                       670    06    037  101122   

  block group  
1           1  
2           2  
3           3  
4           1  
5           2

**Race**


In [121]:
census_codes_all, demo_df2 = get_census_codes('census_df02.parquet',census_rows_df)
census_codes_all
keep_index = [i for i in range(12)]
keep_index
census_codes_all.iloc[keep_index]
df2_mod = create_simplified_df(census_codes_all,keep_index,demo_df2, census_rows_df)
df2_mod.head()

Estimate!!Total: Estimate!!Total:!!Not Hispanic or Latino:  \
1             1415                                      1053   
2             1826                                      1309   
3              773                                       570   
4             2754                                      2610   
5             1410                                      1192   

  Estimate!!Total:!!Not Hispanic or Latino:!!White alone  \
1                                                788       
2                                                949       
3                                                499       
4                                               2043       
5                                                839       

  Estimate!!Total:!!Not Hispanic or Latino:!!Black or African American alone  \
1                                                 91                           
2                                                 30                           
3                                                  0                           
4                                                 68                           
5                                                  8                           

  Estimate!!Total:!!Not Hispanic or Latino:!!American Indian and Alaska Native alone  \
1                                                  0                                   
2                                                  8                                   
3                                                  0                                   
4                                                  0                                   
5                                                  0                                   

  Estimate!!Total:!!Not Hispanic or Latino:!!Asian alone  \
1                                                 68       
2                                                265       
3                                                 57       
4                                                375       
5                                                207       

  Estimate!!Total:!!Not Hispanic or Latino:!!Native Hawaiian and Other Pacific Islander alone  \
1                                                  0                                            
2                                                  0                                            
3                                                  0                                            
4                                                  0                                            
5                                                  0                                            

  Estimate!!Total:!!Not Hispanic or Latino:!!Some other race alone  \
1                                                  0                 
2                                                  8                 
3                                                  0                 
4                                                 12                 
5                                                  0                 

  Estimate!!Total:!!Not Hispanic or Latino:!!Two or more races:  \
1                                                106              
2                                                 49              
3                                                 14              
4                                                112              
5                                                138              

  Estimate!!Total:!!Not Hispanic or Latino:!!Two or more races:!!Two races including Some other race  \
1                                                  0                                                   
2                                                  0                                                   
3                                                  0                                                   
4                                                  0          


**Marital Status**


In [122]:
census_codes_all, demo_df3 = get_census_codes('census_df03.parquet',census_rows_df)
census_codes_all
keep_index = [0,1,2,3,8,9,10,11,12,17,18]
census_codes_all.iloc[keep_index]['Name'].tolist()
df3_mod = create_simplified_df(census_codes_all,keep_index,demo_df3, census_rows_df)
df3_mod.head()

Estimate!!Total: Estimate!!Total:!!Male:  \
1             1152                     568   
2             1654                     804   
3              733                     317   
4             2390                    1186   
5             1225                     673   

  Estimate!!Total:!!Male:!!Never married  \
1                                    221   
2                                    324   
3                                    100   
4                                    321   
5                                    387   

  Estimate!!Total:!!Male:!!Now married: Estimate!!Total:!!Male:!!Widowed  \
1                                   252                               37   
2                                   410                               27   
3                                   184                                0   
4                                   809                               20   
5                                   252                                5   

  Estimate!!Total:!!Male:!!Divorced Estimate!!Total:!!Female:  \
1                                58                       584   
2                                43                       850   
3                                33                       416   
4                                36                      1204   
5                                29                       552   

  Estimate!!Total:!!Female:!!Never married  \
1                                      175   
2                                      251   
3                                      147   
4                                      279   
5                                      102   

  Estimate!!Total:!!Female:!!Now married: Estimate!!Total:!!Female:!!Widowed  \
1                                     214                                136   
2                                     405                                 77   
3                                     182                                 42   
4                                     752                                117   
5                                     278                                 74   

  Estimate!!Total:!!Female:!!Divorced state county   tract block group  
1                                  59    06    037  101110           1  
2                                 117    06    037  101110           2  
3                                  45    06    037  101110           3  
4                                  56    06    037  101122           1  
5                                  98    06    037  101122           2


**Educational Attainment**


In [123]:
census_codes_all, demo_df4 = get_census_codes('census_df04.parquet',census_rows_df)
census_codes_all
keep_index = [i for i in range(0,25)]
census_codes_all.iloc[keep_index]['Name'].tolist()
df4_mod = create_simplified_df(census_codes_all,keep_index,demo_df4, census_rows_df)
df4_mod.head()

Estimate!!Total: Estimate!!Total:!!No schooling completed  \
1              983                                       26   
2             1495                                        9   
3              641                                        0   
4             2030                                      351   
5             1102                                       39   

  Estimate!!Total:!!Nursery school Estimate!!Total:!!Kindergarten  \
1                                0                              0   
2                                0                              0   
3                                0                              0   
4                                0                              0   
5                                0                              0   

  Estimate!!Total:!!1st grade Estimate!!Total:!!2nd grade  \
1                           0                           0   
2                           0                           0   
3                           0                           0   
4                           0                           0   
5                           0                           0   

  Estimate!!Total:!!3rd grade Estimate!!Total:!!4th grade  \
1                           0                           0   
2                          14                           5   
3                           0                           0   
4                           0                           0   
5                           0                           0   

  Estimate!!Total:!!5th grade Estimate!!Total:!!6th grade  ...  \
1                           9                          19  ...   
2                           0                           4  ...   
3                           0                           0  ...   
4                           0                          25  ...   
5                          18                          18  ...   

  Estimate!!Total:!!Some college, 1 or more years, no degree  \
1                                                174           
2                                                255           
3                                                163           
4                                                316           
5                                                271           

  Estimate!!Total:!!Associate's degree Estimate!!Total:!!Bachelor's degree  \
1                                  124                                 292   
2                                  144                                 283   
3                                   65                                 119   
4                                  138                                 403   
5                                   73                                 256   

  Estimate!!Total:!!Master's degree  \
1                                59   
2                                53   
3                                45   
4                               270   
5                                87   

  Estimate!!Total:!!Professional school degree  \
1                                            0   
2                                           11   
3                                           21   
4                                           45   
5                                           16   

  Estimate!!Total:!!Doctorate degree state county   tract block group  
1                                  0    06    037  101110           1  
2                                 19    06    037  101110           2  
3                                  0    06    037  101110           3  
4                                101    06    037  101122           1  
5                                 25    06    037  101122           2  

[5 rows x 29 columns]

**Household Income**


In [124]:
census_codes_all, demo_df5 = get_census_codes('census_df05.parquet',census_rows_df)
census_codes_all
keep_index = [i for i in range(0,17)]
census_codes_all.iloc[keep_index]['Name'].tolist()
df5_mod = create_simplified_df(census_codes_all,keep_index,demo_df5, census_rows_df)
df5_mod.head()

Estimate!!Total: Estimate!!Total:!!Less than $10,000  \
1              574                                  33   
2              653                                  23   
3              324                                  11   
4              830                                  84   
5              553                                   0   

  Estimate!!Total:!!$10,000 to $14,999 Estimate!!Total:!!$15,000 to $19,999  \
1                                   66                                    0   
2                                   20                                   33   
3                                   10                                    0   
4                                    0                                    0   
5                                    0                                    7   

  Estimate!!Total:!!$20,000 to $24,999 Estimate!!Total:!!$25,000 to $29,999  \
1                                   45                                    0   
2                                    0                                   11   
3                                   27                                    0   
4                                    0                                    0   
5                                   44                                   20   

  Estimate!!Total:!!$30,000 to $34,999 Estimate!!Total:!!$35,000 to $39,999  \
1                                   44                                   19   
2                                    0                                    0   
3                                   34                                    0   
4                                   29                                    0   
5                                    0                                    0   

  Estimate!!Total:!!$40,000 to $44,999 Estimate!!Total:!!$45,000 to $49,999  \
1                                   28                                   23   
2                                   28                                   73   
3                                    0                                    0   
4                                    4                                   10   
5                                    0                                    0   

   ... Estimate!!Total:!!$60,000 to $74,999  \
1  ...                                  153   
2  ...                                   46   
3  ...                                   22   
4  ...                                   31   
5  ...                                  177   

  Estimate!!Total:!!$75,000 to $99,999 Estimate!!Total:!!$100,000 to $124,999  \
1                                    9                                     24   
2                                   51                                    115   
3                                   42                                     43   
4                                  126                                     84   
5                                   47                                     18   

  Estimate!!Total:!!$125,000 to $149,999  \
1                                     58   
2                                     64   
3                                     22   
4                                    128   
5                                     53   

  Estimate!!Total:!!$150,000 to $199,999 Estimate!!Total:!!$200,000 or more  \
1                                     29                                 31   
2                                     43                                106   
3                                     51                                 40   
4                                    142                                178   
5                                     62                                108   

  state county   tract block group  
1    06    037  101110           1  
2    06    037  101110           2  
3    06    037  101110           3  
4    06    037  101122           1  
5    06    037  101122           2  

[5 rows x 21 columns

**Employment Status**


In [125]:
census_codes_all, demo_df6 = get_census_codes('census_df06.parquet',census_rows_df)
census_codes_all
keep_index = [i for i in range(0,7)]
census_codes_all.iloc[keep_index]['Name'].tolist()
df6_mod = create_simplified_df(census_codes_all,keep_index,demo_df6, census_rows_df)
df6_mod.head()

Estimate!!Total: Estimate!!Total:!!In labor force:  \
1             1146                               728   
2             1643                              1049   
3              733                               495   
4             2390                              1454   
5             1207                               840   

  Estimate!!Total:!!In labor force:!!Civilian labor force:  \
1                                                728         
2                                               1049         
3                                                495         
4                                               1454         
5                                                840         

  Estimate!!Total:!!In labor force:!!Civilian labor force:!!Employed  \
1                                                688                   
2                                                982                   
3                                                425                   
4                                               1340                   
5                                                734                   

  Estimate!!Total:!!In labor force:!!Civilian labor force:!!Unemployed  \
1                                                 40                     
2                                                 67                     
3                                                 70                     
4                                                114                     
5                                                106                     

  Estimate!!Total:!!In labor force:!!Armed Forces  \
1                                               0   
2                                               0   
3                                               0   
4                                               0   
5                                               0   

  Estimate!!Total:!!Not in labor force state county   tract block group  
1                                  418    06    037  101110           1  
2                                  594    06    037  101110           2  
3                                  238    06    037  101110           3  
4                                  936    06    037  101122           1  
5                                  367    06    037  101122           2

**Occupancy Status**


In [126]:
census_codes_all, demo_df7 = get_census_codes('census_df07.parquet',census_rows_df)
census_codes_all
keep_index = [i for i in range(0,3)]
census_codes_all.iloc[keep_index]['Name'].tolist()
df7_mod = create_simplified_df(census_codes_all,keep_index,demo_df7, census_rows_df)
df7_mod.head()

Estimate!!Total: Estimate!!Total:!!Occupied Estimate!!Total:!!Vacant state  \
1              593                        574                       19    06   
2              735                        653                       82    06   
3              324                        324                        0    06   
4              855                        830                       25    06   
5              572                        553                       19    06   

  county   tract block group  
1    037  101110           1  
2    037  101110           2  
3    037  101110           3  
4    037  101122           1  
5    037  101122           2

**Tenure** 


In [127]:
census_codes_all, demo_df8 = get_census_codes('census_df08.parquet',census_rows_df)
census_codes_all
keep_index = [i for i in range(0,3)]
census_codes_all.iloc[keep_index]['Name'].tolist()
df8_mod = create_simplified_df(census_codes_all,keep_index,demo_df8, census_rows_df)
df8_mod.head()

Estimate!!Total: Estimate!!Total:!!Owner occupied  \
1              574                              284   
2              653                              362   
3              324                              194   
4              830                              674   
5              553                              365   

  Estimate!!Total:!!Renter occupied state county   tract block group  
1                               290    06    037  101110           1  
2                               291    06    037  101110           2  
3                               130    06    037  101110           3  
4                               156    06    037  101122           1  
5                               188    06    037  101122           2

**Health Insurance Coverage**


In [128]:
census_codes_all, demo_df9 = get_census_codes('census_df09.parquet',census_rows_df)
census_codes_all
keep_index = [i for i in range(0,16)]
census_codes_all.iloc[keep_index]['Name'].tolist()
df9_mod = create_simplified_df(census_codes_all,keep_index,demo_df9, census_rows_df)
df9_mod.head()

Estimate!!Total:!!Under 19 years:  \
1                               329   
2                               243   
3                                54   
4                               470   
5                               239   

  Estimate!!Total:!!Under 19 years:!!With one type of health insurance coverage:  \
1                                                259                               
2                                                208                               
3                                                 46                               
4                                                442                               
5                                                239                               

  Estimate!!Total:!!Under 19 years:!!With two or more types of health insurance coverage:  \
1                                                 33                                        
2                                                 25                                        
3                                                  0                                        
4                                                  0                                        
5                                                  0                                        

  Estimate!!Total:!!Under 19 years:!!No health insurance coverage  \
1                                                 37                
2                                                 10                
3                                                  8                
4                                                 28                
5                                                  0                

  Estimate!!Total:!!19 to 34 years:  \
1                               301   
2                               330   
3                               163   
4                               443   
5                               162   

  Estimate!!Total:!!19 to 34 years:!!With one type of health insurance coverage:  \
1                                                273                               
2                                                255                               
3                                                135                               
4                                                431                               
5                                                128                               

  Estimate!!Total:!!19 to 34 years:!!With two or more types of health insurance coverage:  \
1                                                 14                                        
2                                                 75                                        
3                                                 12                                        
4                                                 12                                        
5                                                  0                                        

  Estimate!!Total:!!19 to 34 years:!!No health insurance coverage  \
1                                                 14                
2                                                  0                
3                                                 16                
4                                                  0                
5                                                 34                

  Estimate!!Total:!!35 to 64 years:  \
1                               552   
2                               801   
3                               366   
4                              1219   
5                               720   

  Estimate!!Total:!!35 to 64 years:!!With one type of health insurance coverage:  \
1                                                413                               
2                                                708                               
3                                                296                               
4  

**Computer and Internet Availability**



In [129]:
census_codes_all, demo_df10 = get_census_codes('census_df10.parquet',census_rows_df)
census_codes_all
keep_index = [i for i in range(0,16)]
census_codes_all.iloc[keep_index]['Name'].tolist()
df10_mod = create_simplified_df(census_codes_all,keep_index,demo_df10, census_rows_df)
df10_mod.head()

Estimate!!Total: Estimate!!Total:!!Has a computer:  \
1              574                               537   
2              653                               629   
3              324                               294   
4              830                               807   
5              553                               553   

  Estimate!!Total:!!Has a computer:!!With dial-up Internet subscription alone  \
1                                                  0                            
2                                                  0                            
3                                                  0                            
4                                                 14                            
5                                                  0                            

  Estimate!!Total:!!Has a computer:!!With a broadband Internet subscription  \
1                                                487                          
2                                                594                          
3                                                283                          
4                                                793                          
5                                                544                          

  Estimate!!Total:!!Has a computer:!!Without an Internet subscription  \
1                                                 50                    
2                                                 35                    
3                                                 11                    
4                                                  0                    
5                                                  9                    

  Estimate!!Total:!!No computer Estimate!!Total:  \
1                            37             1404   
2                            24             1734   
3                            30              773   
4                            23             2751   
5                             0             1410   

  Estimate!!Total:!!Has a computer:  \
1                              1367   
2                              1710   
3                               723   
4                              2705   
5                              1410   

  Estimate!!Total:!!Has a computer:!!With dial-up Internet subscription alone  \
1                                                  0                            
2                                                  0                            
3                                                  0                            
4                                                 14                            
5                                                  0                            

  Estimate!!Total:!!Has a computer:!!With a broadband subscription:  \
1                                               1303                  
2                                               1604                  
3                                                700                  
4                                               2691                  
5                                               1401                  

  Estimate!!Total:!!Has a computer:!!With a broadband subscription:!!With a fixed broadband Internet subscription:  \
1                                               1268                                                                 
2                                               1503                                                                 
3                                                641                                                                 
4                                               2469                                                                 
5                                               1379                                                                 

  Estimate!!Total:!!Has a computer:!!With a broadband subscription:!!With a fixed broadband I

**Age**

In [130]:
census_codes_all, demo_df11 = get_census_codes('census_df01.parquet',census_rows_df)
keep_index = [i for i in range(len(census_codes_all))]
df11_mod = create_simplified_df(census_codes_all,keep_index,demo_df11, census_rows_df)
df11_mod.head()

Estimate!!Total: Estimate!!Total:!!Male:  \
1             1415                     677   
2             1826                     884   
3              773                     344   
4             2754                    1358   
5             1410                     740   

  Estimate!!Total:!!Male:!!Under 5 years  \
1                                      7   
2                                     31   
3                                     21   
4                                     35   
5                                     23   

  Estimate!!Total:!!Male:!!5 to 9 years  \
1                                    23   
2                                    23   
3                                     6   
4                                    73   
5                                    23   

  Estimate!!Total:!!Male:!!10 to 14 years  \
1                                      79   
2                                      26   
3                                       0   
4                                      64   
5                                      21   

  Estimate!!Total:!!Male:!!15 to 17 years  \
1                                      66   
2                                      54   
3                                       0   
4                                      33   
5                                      36   

  Estimate!!Total:!!Male:!!18 and 19 years Estimate!!Total:!!Male:!!20 years  \
1                                       31                                 0   
2                                       26                                 0   
3                                       18                                 0   
4                                       42                                24   
5                                       12                                 0   

  Estimate!!Total:!!Male:!!21 years Estimate!!Total:!!Male:!!22 to 24 years  \
1                                 0                                       5   
2                                 0                                      29   
3                                 0                                      18   
4                                24                                      31   
5                                 0                                      57   

   ... Estimate!!Total:!!Female:!!65 and 66 years  \
1  ...                                         42   
2  ...                                         65   
3  ...                                          0   
4  ...                                         71   
5  ...                                         16   

  Estimate!!Total:!!Female:!!67 to 69 years  \
1                                        22   
2                                        43   
3                                        78   
4                                        45   
5                                        66   

  Estimate!!Total:!!Female:!!70 to 74 years  \
1                                        31   
2                                        17   
3                                        16   
4                                        64   
5                                        53   

  Estimate!!Total:!!Female:!!75 to 79 years  \
1                                         0   
2                                        45   
3                                        11   
4                                        45   
5                                        18   

  Estimate!!Total:!!Female:!!80 to 84 years  \
1                                         9   
2                                        16   
3                                        22   
4                                        90   
5                                         0   

  Estimate!!Total:!!Female:!!85 years and over state county   tract  \
1                                           11    06    037  101110   
2                                           23    06    037  101110   
3                                      

**Final Demo DFs**

**Gender**

In [131]:
df1_mod.head()

Estimate!!Total:!!Male: Estimate!!Total:!!Female: state county   tract  \
1                     677                       738    06    037  101110   
2                     884                       942    06    037  101110   
3                     344                       429    06    037  101110   
4                    1358                      1396    06    037  101122   
5                     740                       670    06    037  101122   

  block group  
1           1  
2           2  
3           3  
4           1  
5           2

In [132]:
df1_adj = df1_mod.rename(columns={df1_mod.columns[0]:'gender_male',df1_mod.columns[1]:'gender_female'})

**Race**

Columns:
1. White: 2
2. Black: 3
3. Native American: 4
4. Asian: 5
5. Pacific Islander: 6
6. Other Race: 7
7. Two or More Races:8
8. Hispanic: 11

In [133]:
col_rename = {}
col_rename[df2_mod.columns[2]] = 'race_white'
col_rename[df2_mod.columns[3]] = 'race_black'
col_rename[df2_mod.columns[4]] = 'race_native_american'
col_rename[df2_mod.columns[5]] = 'race_asian'
col_rename[df2_mod.columns[6]] = 'race_pacific_island'
col_rename[df2_mod.columns[7]] = 'race_other'
col_rename[df2_mod.columns[8]] = 'race_two_plus_races'
col_rename[df2_mod.columns[11]] = 'race_hispanic'

In [134]:
df2_adj = df2_mod.rename(columns=col_rename)

In [135]:
exclude_cols = df2_adj.columns[[0,1,9,10]].tolist()

In [136]:
keep_cols = df2_adj.columns[~df2_adj.columns.isin(exclude_cols)].tolist()

In [137]:
df2_adj = df2_adj.loc[:,keep_cols]

**Marital Status**

Columns:
1. Never Married: 2,7
2. Now Married: 3,8
3. Widowed: 4,9
4. Divorced: 5,10

In [138]:
df3_adj = df3_mod.copy()

In [139]:
df3_adj['marital_status_never_married'] = df3_mod.apply(lambda x: int(x[df3_mod.columns[2]])+int(x[df3_mod.columns[7]]),axis=1)
df3_adj['marital_status_married'] = df3_mod.apply(lambda x: int(x[df3_mod.columns[3]])+int(x[df3_mod.columns[8]]),axis=1)
df3_adj['marital_status_widowed'] = df3_mod.apply(lambda x: int(x[df3_mod.columns[4]])+int(x[df3_mod.columns[9]]),axis=1)
df3_adj['marital_status_divorced'] = df3_mod.apply(lambda x: int(x[df3_mod.columns[5]])+int(x[df3_mod.columns[10]]),axis=1)

In [140]:
df3_adj

Estimate!!Total: Estimate!!Total:!!Male:  \
1                1152                     568   
2                1654                     804   
3                 733                     317   
4                2390                    1186   
5                1225                     673   
...               ...                     ...   
6587                0                       0   
6588                0                       0   
6589                0                       0   
6590                0                       0   
6591                0                       0   

     Estimate!!Total:!!Male:!!Never married  \
1                                       221   
2                                       324   
3                                       100   
4                                       321   
5                                       387   
...                                     ...   
6587                                      0   
6588                                      0   
6589                                      0   
6590                                      0   
6591                                      0   

     Estimate!!Total:!!Male:!!Now married: Estimate!!Total:!!Male:!!Widowed  \
1                                      252                               37   
2                                      410                               27   
3                                      184                                0   
4                                      809                               20   
5                                      252                                5   
...                                    ...                              ...   
6587                                     0                                0   
6588                                     0                                0   
6589                                     0                                0   
6590                                     0                                0   
6591                                     0                                0   

     Estimate!!Total:!!Male:!!Divorced Estimate!!Total:!!Female:  \
1                                   58                       584   
2                                   43                       850   
3                                   33                       416   
4                                   36                      1204   
5                                   29                       552   
...                                ...                       ...   
6587                                 0                         0   
6588                                 0                         0   
6589                                 0                         0   
6590                                 0                         0   
6591                                 0                         0   

     Estimate!!Total:!!Female:!!Never married  \
1                                         175   
2                                         251   
3                                         147   
4                                         279   
5                                         102   
...                                       ...   
6587                                        0   
6588                                        0   
6589                                        0   
6590                                        0   
6591                                        0   

     Estimate!!Total:!!Female:!!Now married:  \
1                                        214   
2                                        405   
3                                        182   
4                                        752   
5                                        278   
...                                      ...   
6587                                       0   
6588                                       0   
6589                                       0   
6590            

In [141]:
exclude_cols = df3_adj.columns[0:11].tolist()

In [142]:
keep_cols = df3_adj.columns[~df3_adj.columns.isin(exclude_cols)].tolist()

In [143]:
df3_adj = df3_adj.loc[:,keep_cols]

In [144]:
df3_adj

state county   tract block group  marital_status_never_married  \
1       06    037  101110           1                           396   
2       06    037  101110           2                           575   
3       06    037  101110           3                           247   
4       06    037  101122           1                           600   
5       06    037  101122           2                           489   
...    ...    ...     ...         ...                           ...   
6587    06    037  980038           1                             0   
6588    06    037  980039           1                             0   
6589    06    037  990100           0                             0   
6590    06    037  990200           0                             0   
6591    06    037  990300           0                             0   

      marital_status_married  marital_status_widowed  marital_status_divorced  
1                        466                     173                      117  
2                        815                     104                      160  
3                        366                      42                       78  
4                       1561                     137                       92  
5                        530                      79                      127  
...                      ...                     ...                      ...  
6587                       0                       0                        0  
6588                       0                       0                        0  
6589                       0                       0                        0  
6590                       0                       0                        0  
6591                       0                       0                        0  

[6591 rows x 8 columns]

**Educational Attainment**

For education, will change groups to:
- No Schooling: 1
- Less than High School: 2-->15
- High School or Equivalent: 16,17
- Some Collegee - No Degree: 18,19
- Associate's Degree: 20
- Bachelor's Degree: 21
- Master's Degree: 22
- Professional School Degree: 23
- Doctorate Degree: 24

In [145]:
df4_adj = df4_mod.copy()

In [146]:
df4_mod.head()

Estimate!!Total: Estimate!!Total:!!No schooling completed  \
1              983                                       26   
2             1495                                        9   
3              641                                        0   
4             2030                                      351   
5             1102                                       39   

  Estimate!!Total:!!Nursery school Estimate!!Total:!!Kindergarten  \
1                                0                              0   
2                                0                              0   
3                                0                              0   
4                                0                              0   
5                                0                              0   

  Estimate!!Total:!!1st grade Estimate!!Total:!!2nd grade  \
1                           0                           0   
2                           0                           0   
3                           0                           0   
4                           0                           0   
5                           0                           0   

  Estimate!!Total:!!3rd grade Estimate!!Total:!!4th grade  \
1                           0                           0   
2                          14                           5   
3                           0                           0   
4                           0                           0   
5                           0                           0   

  Estimate!!Total:!!5th grade Estimate!!Total:!!6th grade  ...  \
1                           9                          19  ...   
2                           0                           4  ...   
3                           0                           0  ...   
4                           0                          25  ...   
5                          18                          18  ...   

  Estimate!!Total:!!Some college, 1 or more years, no degree  \
1                                                174           
2                                                255           
3                                                163           
4                                                316           
5                                                271           

  Estimate!!Total:!!Associate's degree Estimate!!Total:!!Bachelor's degree  \
1                                  124                                 292   
2                                  144                                 283   
3                                   65                                 119   
4                                  138                                 403   
5                                   73                                 256   

  Estimate!!Total:!!Master's degree  \
1                                59   
2                                53   
3                                45   
4                               270   
5                                87   

  Estimate!!Total:!!Professional school degree  \
1                                            0   
2                                           11   
3                                           21   
4                                           45   
5                                           16   

  Estimate!!Total:!!Doctorate degree state county   tract block group  
1                                  0    06    037  101110           1  
2                                 19    06    037  101110           2  
3                                  0    06    037  101110           3  
4                                101    06    037  101122           1  
5                                 25    06    037  101122           2  

[5 rows x 29 columns]

In [147]:
df4_adj['education_less_than_hs'] = df4_mod.apply(lambda x: int(x[df4_mod.columns[2]])+int(x[df4_mod.columns[3]])+int(x[df4_mod.columns[4]])+int(x[df4_mod.columns[2]])\
    +int(x[df4_mod.columns[5]])+int(x[df4_mod.columns[6]])+int(x[df4_mod.columns[7]])+int(x[df4_mod.columns[8]])\
        +int(x[df4_mod.columns[9]])+int(x[df4_mod.columns[10]])+int(x[df4_mod.columns[11]])+int(x[df4_mod.columns[12]])\
            +int(x[df4_mod.columns[13]])+int(x[df4_mod.columns[14]])+int(x[df4_mod.columns[15]]),axis=1)

df4_adj['education_hs'] = df4_mod.apply(lambda x: int(x[df4_mod.columns[16]])+int(x[df4_mod.columns[17]]),axis=1)
df4_adj['education_some_college_no_degree'] = df4_mod.apply(lambda x: int(x[df4_mod.columns[18]])+int(x[df4_mod.columns[19]]),axis=1)

In [148]:
col_rename = {}
col_rename[df4_adj.columns[1]] = 'education_no_schooling'
col_rename[df4_adj.columns[20]] = 'education_associates'
col_rename[df4_adj.columns[21]] = 'education_bachelors'
col_rename[df4_adj.columns[22]] = 'education_masters'
col_rename[df4_adj.columns[23]] = 'education_professional'
col_rename[df4_adj.columns[24]] = 'education_doctorate'


In [149]:

col_rename

{'Estimate!!Total:!!No schooling completed': 'education_no_schooling',
 "Estimate!!Total:!!Associate's degree": 'education_associates',
 "Estimate!!Total:!!Bachelor's degree": 'education_bachelors',
 "Estimate!!Total:!!Master's degree": 'education_masters',
 'Estimate!!Total:!!Professional school degree': 'education_professional',
 'Estimate!!Total:!!Doctorate degree': 'education_doctorate'}

In [150]:
df4_adj = df4_adj.rename(columns=col_rename)

In [151]:
def clean_cell_cols(df_adj):

    new_df = df_adj.copy()

    col_names = new_df.columns.tolist()
    exclude_cols = [re.findall('Estimate.+',col)[0] for col in col_names if len(re.findall('Estimate.+',col)) > 0]
    keep_cols = new_df.columns[~new_df.columns.isin(exclude_cols)].tolist()
    new_df = new_df.loc[:,keep_cols]

    return new_df

In [152]:
df4_adj = clean_cell_cols(df4_adj)

**Income**

Columns:
- Less than $50,000 - 1-->9
- $50,000 - $100,000 - 10-->12
- $100,000 - $150,000 - 13,14
- $150,000 - $200,000 - 15
- $200,000+ - 16

In [153]:
df5_adj = df5_mod.copy()

In [154]:
df5_adj['income_less_than_50k'] = df5_adj.apply(lambda x: int(x[df5_adj.columns[1]])+int(x[df5_adj.columns[2]])+int(x[df5_adj.columns[3]])+int(x[df5_adj.columns[4]])\
    +int(x[df5_adj.columns[5]])+int(x[df5_adj.columns[6]])+int(x[df5_adj.columns[7]])+int(x[df5_adj.columns[8]])\
        +int(x[df5_adj.columns[9]]),axis=1)

df5_adj['income_between_50k_100k'] = df5_adj.apply(lambda x: int(x[df5_adj.columns[10]])+int(x[df5_adj.columns[11]])+int(x[df5_adj.columns[12]]),axis=1)
df5_adj['income_between_100k_150k'] = df5_adj.apply(lambda x: int(x[df5_adj.columns[13]])+int(x[df5_adj.columns[14]]),axis=1)

In [155]:
col_rename = {}
col_rename[df5_adj.columns[15]] = 'income_between_150k_200k'
col_rename[df5_adj.columns[16]] = 'income_over_200k'


In [156]:
df5_adj = df5_adj.rename(columns=col_rename)

In [157]:
df5_adj = clean_cell_cols(df5_adj)

In [158]:
df5_adj

income_between_150k_200k income_over_200k state county   tract  \
1                          29               31    06    037  101110   
2                          43              106    06    037  101110   
3                          51               40    06    037  101110   
4                         142              178    06    037  101122   
5                          62              108    06    037  101122   
...                       ...              ...   ...    ...     ...   
6587                        0                0    06    037  980038   
6588                        0                0    06    037  980039   
6589                        0                0    06    037  990100   
6590                        0                0    06    037  990200   
6591                        0                0    06    037  990300   

     block group  income_less_than_50k  income_between_50k_100k  \
1              1                   258                      174   
2              2                   188                      137   
3              3                    82                       86   
4              1                   127                      171   
5              2                    71                      241   
...          ...                   ...                      ...   
6587           1                     0                        0   
6588           1                     0                        0   
6589           0                     0                        0   
6590           0                     0                        0   
6591           0                     0                        0   

      income_between_100k_150k  
1                           82  
2                          179  
3                           65  
4                          212  
5                           71  
...                        ...  
6587                         0  
6588                         0  
6589                         0  
6590                         0  
6591                         0  

[6591 rows x 9 columns]

**Labor Force**

Columns:
- Employed - 3
- Unemployed - 4
- Armed Forces - 5
- Not in Labor Force - 6

In [159]:
df6_adj = df6_mod.copy()

In [160]:
col_rename = {}
col_rename[df6_adj.columns[3]] = 'employment_employed'
col_rename[df6_adj.columns[4]] = 'employment_unemployed'
col_rename[df6_adj.columns[5]] = 'employment_armed_forces'
col_rename[df6_adj.columns[6]] = 'employment_not_in_labor_force'


In [161]:

col_rename

{'Estimate!!Total:!!In labor force:!!Civilian labor force:!!Employed': 'employment_employed',
 'Estimate!!Total:!!In labor force:!!Civilian labor force:!!Unemployed': 'employment_unemployed',
 'Estimate!!Total:!!In labor force:!!Armed Forces': 'employment_armed_forces',
 'Estimate!!Total:!!Not in labor force': 'employment_not_in_labor_force'}

In [162]:
df6_adj = df6_adj.rename(columns=col_rename)

In [163]:
df6_adj = clean_cell_cols(df6_adj)

In [164]:
df6_adj.head()

employment_employed employment_unemployed employment_armed_forces  \
1                 688                    40                       0   
2                 982                    67                       0   
3                 425                    70                       0   
4                1340                   114                       0   
5                 734                   106                       0   

  employment_not_in_labor_force state county   tract block group  
1                           418    06    037  101110           1  
2                           594    06    037  101110           2  
3                           238    06    037  101110           3  
4                           936    06    037  101122           1  
5                           367    06    037  101122           2

**Tenure**

Columns:
1. Home Owner - 1
2. Renter - 2

In [165]:
df8_adj = df8_mod.copy()

In [166]:
col_rename = {}
col_rename[df8_adj.columns[1]] = 'tenure_home_owner'
col_rename[df8_adj.columns[2]] = 'tenure_renter'

In [167]:

col_rename

{'Estimate!!Total:!!Owner occupied': 'tenure_home_owner',
 'Estimate!!Total:!!Renter occupied': 'tenure_renter'}

In [168]:
df8_adj = df8_adj.rename(columns=col_rename)

In [169]:
df8_adj = clean_cell_cols(df8_adj)

In [170]:
df8_adj.head()

tenure_home_owner tenure_renter state county   tract block group
1               284           290    06    037  101110           1
2               362           291    06    037  101110           2
3               194           130    06    037  101110           3
4               674           156    06    037  101122           1
5               365           188    06    037  101122           2

**Health Insurance**

Columns:
1. One type of coverage - 1,5,9,13,
2. Two or more types of coverage - 2,6,10,14
3. No covereage - 3,7,11,15

In [171]:
df9_adj = df9_mod.copy()

In [172]:
df9_adj['health_insurance_one_type'] = df9_adj.apply(lambda x: int(x[df9_adj.columns[1]])+int(x[df9_adj.columns[5]])+int(x[df9_adj.columns[9]])\
        +int(x[df9_adj.columns[13]]),axis=1)

df9_adj['health_insurance_two_plus_types'] = df9_adj.apply(lambda x: int(x[df9_adj.columns[2]])+int(x[df9_adj.columns[6]])+int(x[df9_adj.columns[10]])\
        +int(x[df9_adj.columns[14]]),axis=1)

df9_adj['health_insurance_no_coverage'] = df9_adj.apply(lambda x: int(x[df9_adj.columns[3]])+int(x[df9_adj.columns[7]])+int(x[df9_adj.columns[11]])\
        +int(x[df9_adj.columns[15]]),axis=1)

In [173]:
df9_adj = clean_cell_cols(df9_adj)

In [174]:
df9_adj

state county   tract block group  health_insurance_one_type  \
1       06    037  101110           1                       1014   
2       06    037  101110           2                       1300   
3       06    037  101110           3                        560   
4       06    037  101122           1                       2214   
5       06    037  101122           2                       1098   
...    ...    ...     ...         ...                        ...   
6587    06    037  980038           1                          0   
6588    06    037  980039           1                          0   
6589    06    037  990100           0                          0   
6590    06    037  990200           0                          0   
6591    06    037  990300           0                          0   

      health_insurance_two_plus_types  health_insurance_no_coverage  
1                                 307                            94  
2                                 415                            24  
3                                 155                            58  
4                                 501                            36  
5                                 173                           139  
...                               ...                           ...  
6587                                0                             0  
6588                                0                             0  
6589                                0                             0  
6590                                0                             0  
6591                                0                             0  

[6591 rows x 7 columns]

**Computer and Internet Access**

Columns:
- Has Computer: 7
- No Computer: 15
- Internet - Fixed Broadband - 10
- Internet - Dial-up or Cellular Data - 13
- Internet - No Internet Subscription - 14

In [175]:
df10_mod

Estimate!!Total: Estimate!!Total:!!Has a computer:  \
1                 574                               537   
2                 653                               629   
3                 324                               294   
4                 830                               807   
5                 553                               553   
...               ...                               ...   
6587                0                                 0   
6588                0                                 0   
6589                0                                 0   
6590                0                                 0   
6591                0                                 0   

     Estimate!!Total:!!Has a computer:!!With dial-up Internet subscription alone  \
1                                                     0                            
2                                                     0                            
3                                                     0                            
4                                                    14                            
5                                                     0                            
...                                                 ...                            
6587                                                  0                            
6588                                                  0                            
6589                                                  0                            
6590                                                  0                            
6591                                                  0                            

     Estimate!!Total:!!Has a computer:!!With a broadband Internet subscription  \
1                                                   487                          
2                                                   594                          
3                                                   283                          
4                                                   793                          
5                                                   544                          
...                                                 ...                          
6587                                                  0                          
6588                                                  0                          
6589                                                  0                          
6590                                                  0                          
6591                                                  0                          

     Estimate!!Total:!!Has a computer:!!Without an Internet subscription  \
1                                                    50                    
2                                                    35                    
3                                                    11                    
4                                                     0                    
5                                                     9                    
...                                                 ...                    
6587                                                  0                    
6588                                                  0                    
6589                                                  0                    
6590                                                  0                    
6591                                                  0                    

     Estimate!!Total:!!No computer Estimate!!Total:  \
1                               37             1404   
2                               24             1734   
3                               30              773   
4                               23             2751   
5                                0             1410   
...                            ...              ...   
6587

In [176]:
df10_adj = df10_mod.copy()

In [177]:
col_rename = {}
col_rename[df10_adj.columns[7]] = 'computer_has_computer'
col_rename[df10_adj.columns[15]] = 'computer_no_computer'

col_rename[df10_adj.columns[10]] = 'internet_fixed_broadband'
col_rename[df10_adj.columns[13]] = 'internet_dial_up_or_cellular'
col_rename[df10_adj.columns[14]] = 'internet_no_internet'


In [178]:
col_rename

{'Estimate!!Total:!!Has a computer:': 'computer_has_computer',
 'Estimate!!Total:!!No Computer': 'computer_no_computer',
 'Estimate!!Total:!!Has a computer:!!With a broadband subscription:!!With a fixed broadband Internet subscription:': 'internet_fixed_broadband',
 'Estimate!!Total:!!Has a computer:!!With a broadband subscription:!!Cellular data plan alone or with dial-up': 'internet_dial_up_or_cellular',
 'Estimate!!Total:!!Has a computer:!!Without Internet subscription': 'internet_no_internet'}

In [179]:
l = [i for i in range(len(df10_adj.columns))]

In [180]:
l.remove(5)
l.remove(1)
l.remove(4)


In [181]:
l

[0, 2, 3, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19]

In [182]:
df10_adj = df10_adj.iloc[:,l].copy()

In [183]:
col_rename

{'Estimate!!Total:!!Has a computer:': 'computer_has_computer',
 'Estimate!!Total:!!No Computer': 'computer_no_computer',
 'Estimate!!Total:!!Has a computer:!!With a broadband subscription:!!With a fixed broadband Internet subscription:': 'internet_fixed_broadband',
 'Estimate!!Total:!!Has a computer:!!With a broadband subscription:!!Cellular data plan alone or with dial-up': 'internet_dial_up_or_cellular',
 'Estimate!!Total:!!Has a computer:!!Without Internet subscription': 'internet_no_internet'}

In [184]:
df10_adj = df10_adj.rename(columns=col_rename)

In [185]:
df10_adj

Estimate!!Total:  \
1                 574   
2                 653   
3                 324   
4                 830   
5                 553   
...               ...   
6587                0   
6588                0   
6589                0   
6590                0   
6591                0   

     Estimate!!Total:!!Has a computer:!!With dial-up Internet subscription alone  \
1                                                     0                            
2                                                     0                            
3                                                     0                            
4                                                    14                            
5                                                     0                            
...                                                 ...                            
6587                                                  0                            
6588                                                  0                            
6589                                                  0                            
6590                                                  0                            
6591                                                  0                            

     Estimate!!Total:!!Has a computer:!!With a broadband Internet subscription  \
1                                                   487                          
2                                                   594                          
3                                                   283                          
4                                                   793                          
5                                                   544                          
...                                                 ...                          
6587                                                  0                          
6588                                                  0                          
6589                                                  0                          
6590                                                  0                          
6591                                                  0                          

     Estimate!!Total: computer_has_computer  \
1                1404                  1367   
2                1734                  1710   
3                 773                   723   
4                2751                  2705   
5                1410                  1410   
...               ...                   ...   
6587                0                     0   
6588                0                     0   
6589                0                     0   
6590                0                     0   
6591                0                     0   

     Estimate!!Total:!!Has a computer:!!With dial-up Internet subscription alone  \
1                                                     0                            
2                                                     0                            
3                                                     0                            
4                                                    14                            
5                                                     0                            
...                                                 ...                            
6587                                                  0                            
6588                                                  0                            
6589                                                  0                            
6590                                                  0                            
6591                                                  0                            

     Estimate!!Total:!!Has a computer:!!With a broadband subscription:  \
1                                                  1303       

In [186]:
df10_adj = clean_cell_cols(df10_adj)

In [187]:
df10_adj.head()

computer_has_computer internet_fixed_broadband internet_dial_up_or_cellular  \
1                  1367                     1268                           35   
2                  1710                     1503                          101   
3                   723                      641                           59   
4                  2705                     2469                          222   
5                  1410                     1379                           22   

  internet_no_internet computer_no_computer state county   tract block group  
1                   64                   37    06    037  101110           1  
2                  106                   24    06    037  101110           2  
3                   23                   50    06    037  101110           3  
4                    0                   46    06    037  101122           1  
5                    9                    0    06    037  101122           2

**Age**

Columns:
- 18 - 24: 6,7,8,9,30,31,32,33
- 25 - 34: 10,11,34,35
- 35 - 44: 12,13,36,37
- 45 - 54: 14,15,38,39
- 55 - 64: 16,17,18,40,41,42
- 65+ 19,20,21,22,23,24,43,44,45,46,47,48

In [188]:
df11_adj = df11_mod.copy()

In [189]:
group1 = [6,7,8,9,30,31,32,33]
group2 = [10,11,34,35]
group3 = [12,13,36,37]
group4 = [14,15,38,39]
group5 = [16,17,18,40,41,42]
group6 = [19,20,21,22,23,24,43,45,46,47,48]

label_cols = [49,50,51,52]

In [190]:
group1_df = df11_adj.iloc[:,group1].astype('int').apply(lambda x: x.sum(),axis=1)
group2_df = df11_adj.iloc[:,group2].astype('int').apply(lambda x: x.sum(),axis=1)
group3_df = df11_adj.iloc[:,group3].astype('int').apply(lambda x: x.sum(),axis=1)
group4_df = df11_adj.iloc[:,group4].astype('int').apply(lambda x: x.sum(),axis=1)
group5_df = df11_adj.iloc[:,group5].astype('int').apply(lambda x: x.sum(),axis=1)
group6_df = df11_adj.iloc[:,group6].astype('int').apply(lambda x: x.sum(),axis=1)
group7_df = df11_adj.iloc[:,label_cols]

In [191]:
df11_adj = pd.concat([group1_df, group2_df, group3_df,group4_df, group5_df, group6_df, group7_df],axis=1)

In [192]:
col_rename = {}
col_rename[0] = 'age_18_to_24'
col_rename[1] = 'age_25_to_34'

col_rename[2] = 'age_35_to_44'
col_rename[3] = 'age_45_to_54'
col_rename[4] = 'age_55_to_64'
col_rename[5] = 'age_65+'

In [193]:
df11_adj = df11_adj.rename(columns=col_rename)

In [194]:
df11_adj

age_18_to_24  age_25_to_34  age_35_to_44  age_45_to_54  age_55_to_64  \
1              103           198           104           234           214   
2              105           252           260           252           314   
3               92            85           169           147            50   
4              298           190           224           422           574   
5               69            93           229           262           229   
...            ...           ...           ...           ...           ...   
6587             0             0             0             0             0   
6588             0             0             0             0             0   
6589             0             0             0             0             0   
6590             0             0             0             0             0   
6591             0             0             0             0             0   

      age_65+ state county   tract block group  
1         211    06    037  101110           1  
2         374    06    037  101110           2  
3         112    06    037  101110           3  
4         575    06    037  101122           1  
5         223    06    037  101122           2  
...       ...   ...    ...     ...         ...  
6587        0    06    037  980038           1  
6588        0    06    037  980039           1  
6589        0    06    037  990100           0  
6590        0    06    037  990200           0  
6591        0    06    037  990300           0  

[6591 rows x 10 columns]

In [195]:
def create_features_df(input_df):
    
    location_columns = ['tract','block group']
    
    adj_df = input_df.loc[:,~input_df.columns.isin(['state','county'])].copy()
    
    adj_df_select = adj_df.iloc[:, ~adj_df.columns.isin(location_columns)].astype('float')
    cols = adj_df_select.columns.tolist() 
    
    adj_df.loc[:,cols] = adj_df.loc[:,cols].astype('float64')
    adj_df[cols] = adj_df_select
    
    
    adj_df_a = adj_df.groupby('tract').sum().reset_index()
    adj_df_b = adj_df_a.loc[:,~adj_df_a.columns.isin(['block group'])].copy()
    
    
    
    adj_df_b['total'] = adj_df_b.iloc[:, ~adj_df_b.columns.isin(['tract'])].apply(lambda x: x.sum(),axis=1)
    
    

    
    adj_df_c = adj_df_b.loc[adj_df_b['total'] > 0].copy()
    
    
    adj_df_d = adj_df_c.loc[:, ~adj_df_c.columns.isin(location_columns)].div(adj_df_c['total'],axis=0).copy()
    
    
    cols = adj_df_d.columns.tolist()
    
    
    adj_df_e = adj_df_c.copy()
    
    

    adj_df_e.loc[:,cols] = adj_df_d
    

    return adj_df_e.loc[:,~adj_df_e.columns.isin(['total'])]
    

In [196]:
def create_features_df_totals(input_df):
    
    location_columns = ['tract','block group']
    #excl_cols = input_df.columns[~input_df.columns.isin(location_columns)].tolist()
    #adj_df = input_df.iloc[:, ~input_df.columns.isin(location_columns)]
    adj_df = input_df.loc[:,~input_df.columns.isin(['state','county'])].copy()
    #adj_df.iloc[:, ~adj_df.columns.isin(location_columns)] = adj_df.iloc[:, ~adj_df.columns.isin(location_columns)].astype('float')
    adj_df_select = adj_df.iloc[:, ~adj_df.columns.isin(location_columns)].astype('float')
    cols = adj_df_select.columns.tolist() 
    #print(adj_df_select.head())
    adj_df.loc[:,cols] = adj_df.loc[:,cols].astype('float64')
    adj_df[cols] = adj_df_select
    #adj_df.loc[:,cols] = adj_df_select
    #print(adj_df.head().dtypes)
    #adj_df.loc[:,cols] = adj_df.loc[:,cols].astype('float')
    #print(adj_df.loc[:,cols].head())
    adj_df_a = adj_df.groupby('tract').sum().reset_index()
    adj_df_b = adj_df_a.loc[:,~adj_df_a.columns.isin(['block group'])].copy()
    
    
    
    adj_df_b['total'] = adj_df_b.iloc[:, ~adj_df_b.columns.isin(['tract'])].apply(lambda x: x.sum(),axis=1)
    
    

    
    adj_df_c = adj_df_b.loc[adj_df_b['total'] > 0].copy()
    #print(adj_df_c)

    '''
    adj_df_d = adj_df_c.loc[:, ~adj_df_c.columns.isin(location_columns)].div(adj_df_c['total'],axis=0).copy()
    
    
    cols = adj_df_d.columns.tolist()
    
    
    adj_df_e = adj_df_c.copy()
    #print(adj_df_select.head())
    

    adj_df_e.loc[:,cols] = adj_df_d
    #print(adj_df_e)
    '''
    return adj_df_c
    
    

In [197]:
modified_dfs = [df1_adj,df2_adj,df3_adj,df4_adj,df5_adj,df6_adj,df8_adj,df9_adj,df10_adj,df11_adj]

In [198]:
df_totals_list = []

for i in range(len(modified_dfs)):
    
    df_totals_list.append(create_features_df_totals(modified_dfs[i])) 

In [199]:
m1_total = pd.merge(df_totals_list[0],df_totals_list[1].loc[:,~df_totals_list[1].columns.isin(['total'])],how='left', left_on='tract', right_on='tract')
m2_total = pd.merge(m1_total,df_totals_list[2].loc[:,~df_totals_list[2].columns.isin(['total'])],how='left', left_on='tract', right_on='tract')
m3_total = pd.merge(m2_total,df_totals_list[3].loc[:,~df_totals_list[3].columns.isin(['total'])],how='left', left_on='tract', right_on='tract')
m4_total = pd.merge(m3_total,df_totals_list[4].loc[:,~df_totals_list[4].columns.isin(['total'])],how='left', left_on='tract', right_on='tract')
m5_total = pd.merge(m4_total,df_totals_list[5].loc[:,~df_totals_list[5].columns.isin(['total'])],how='left', left_on='tract', right_on='tract')
m6_total = pd.merge(m5_total,df_totals_list[6].loc[:,~df_totals_list[6].columns.isin(['total'])],how='left', left_on='tract', right_on='tract')
m7_total = pd.merge(m6_total,df_totals_list[7].loc[:,~df_totals_list[7].columns.isin(['total'])],how='left', left_on='tract', right_on='tract')
m8_total = pd.merge(m7_total,df_totals_list[8].loc[:,~df_totals_list[8].columns.isin(['total'])],how='left', left_on='tract', right_on='tract')
m9_total = pd.merge(m8_total,df_totals_list[9].loc[:,~df_totals_list[9].columns.isin(['total'])],how='left', left_on='tract', right_on='tract')


In [200]:
m9_total.head()

tract  gender_male  gender_female   total  race_white  race_black  \
0  101110       1905.0         2109.0  4014.0      2236.0       121.0   
1  101122       2098.0         2066.0  4164.0      2882.0        76.0   
2  101220       1651.0         1830.0  3481.0      1485.0         0.0   
3  101221       1966.0         1790.0  3756.0      1970.0       101.0   
4  101222       1266.0         1542.0  2808.0      1277.0        15.0   

   race_native_american  race_asian  race_pacific_island  race_other  ...  \
0                   8.0       390.0                  0.0         8.0  ...   
1                   0.0       582.0                  0.0        12.0  ...   
2                  46.0       433.0                  0.0         5.0  ...   
3                   0.0       314.0                  0.0       107.0  ...   
4                   0.0       138.0                 37.0         0.0  ...   

   internet_fixed_broadband  internet_dial_up_or_cellular  \
0                    3412.0                         195.0   
1                    3848.0                         244.0   
2                    2566.0                         456.0   
3                    2667.0                         449.0   
4                    1716.0                          43.0   

   internet_no_internet  computer_no_computer  age_18_to_24  age_25_to_34  \
0                 193.0                 111.0         300.0         535.0   
1                   9.0                  46.0         367.0         283.0   
2                 282.0                 177.0         325.0         455.0   
3                 164.0                 387.0         380.0         439.0   
4                 985.0                  64.0         206.0         580.0   

   age_35_to_44  age_45_to_54  age_55_to_64  age_65+  
0         533.0         633.0         578.0    697.0  
1         453.0         684.0         803.0    798.0  
2         417.0         625.0         494.0    519.0  
3         628.0         436.0         446.0    684.0  
4         265.0         512.0         274.0    418.0  

[5 rows x 50 columns]

In [201]:
m9_total['tract'] = m9_total['tract'].astype('int')

In [202]:
parquet_file = 'census_features_total.parquet'
m9_total.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

In [203]:
del demo_df1,demo_df10, demo_df11,demo_df2, demo_df3, demo_df4, demo_df5,demo_df6, demo_df7
del demo_df8, demo_df9, df1_adj, df1_mod, df10_adj, df10_mod, df11_adj, df11_mod, df2_adj
del df2_mod, df3_adj, df3_mod, df4_adj, df4_mod, df5_adj, df5_mod, df6_adj, df6_mod, df7_mod
del df8_adj, df8_mod, df9_adj, df9_mod

In [204]:
del census_codes_all, census_concepts_df, census_rows_df, census_variables

In [205]:
del df_totals_list, group1, group1_df, group2, group2_df, group3, group3_df, group4, group4_df
del group5, group5_df, group6, group6_df, group7_df, m1_total, m2_total, m3_total, m4_total
del m5_total, m6_total,m7_total, m8_total

In [206]:
del results_df

##### **2.4 Precinct & Census Tract Mapping**

**Create the mapping file used to connect census demographic data to voter preincts**

Main data source for this mapping are precinct mapping files provided by [Statewide Datatabase](https://statewidedatabase.org/)





In [355]:
response = s3.list_objects(Bucket= my_bucket, Prefix="raw_files/precinct_mapping")
files = response.get("Contents")


In [356]:
key_list = []
for item in files:
    if re.search('.csv',item['Key']) != None:
        key_list.append(item['Key'])

In [357]:
temp_file = "tempfile.csv"
precinct_df = pd.DataFrame()



for key in key_list:
    
    general_election = re.findall('g\d{2}', key)
    primary_election = re.findall('p\d{2}', key)

    if general_election:    
        election_year = re.findall('\d{2}',general_election[0])[0]
        election_type = 'general'
        print('General Election:', key, election_year)
    
    elif primary_election:
        election_year = re.findall('\d{2}',primary_election[0])[0]
        print('Primary Election:', key, election_year)
        election_type = 'primary'
    
    keep_cols = [0,1,2,3,6]
    new_colnames = ['precinct','census_tract','census_block','block_group1','block_group2']
    

    

    s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=key)
    

    file_df = pd.read_csv(temp_file)
    
    keep_df = file_df.iloc[1:,keep_cols]
    keep_df = keep_df.set_axis(new_colnames, axis='columns')
    
    keep_df['filename'] = file
    keep_df['election_year'] = election_year
    keep_df['election_type'] = election_type

    precinct_df = pd.concat([precinct_df,keep_df],axis=0)
    

General Election: raw_files/precinct_mapping/c037_g14_rg_blk_map.csv 14
General Election: raw_files/precinct_mapping/c037_g14_sr_blk_map.csv 14
General Election: raw_files/precinct_mapping/c037_g16_rg_blk_map.csv 16
General Election: raw_files/precinct_mapping/c037_g16_sr_blk_map.csv 16
General Election: raw_files/precinct_mapping/c037_g18_rg_blk_map.csv 18
General Election: raw_files/precinct_mapping/c037_g18_sr_blk_map.csv 18
General Election: raw_files/precinct_mapping/c037_g20_rg_blk_map.csv 20
General Election: raw_files/precinct_mapping/c037_g20_sr_blk_map.csv 20
General Election: raw_files/precinct_mapping/c037_g22_rg_blk_map.csv 22
General Election: raw_files/precinct_mapping/c037_g22_sr_blk_map.csv 22
Primary Election: raw_files/precinct_mapping/c037_p14_rg_blk_map.csv 14
Primary Election: raw_files/precinct_mapping/c037_p14_sr_blk_map.csv 14
Primary Election: raw_files/precinct_mapping/c037_p16_rg_blk_map.csv 16
Primary Election: raw_files/precinct_mapping/c037_p16_sr_blk_map

In [358]:
del keep_df, file_df, general_election, primary_election, new_colnames, election_year, election_type

In [359]:
precinct_df = precinct_df.reset_index(drop=True)

In [360]:
parquet_file = 'precinct_info.parquet'
precinct_df.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

In [361]:
a = precinct_df.iloc[:,[0,1]].drop_duplicates().reset_index(drop=True).copy()

In [362]:
a = precinct_df[precinct_df['election_year'] == '22'].loc[:,['precinct','census_tract']].drop_duplicates().reset_index(drop=True)

In [218]:
parquet_file = 'precinct_census_mapping.parquet'
a.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

**Map Census Tract Features with Precincts**

The combination work needs to happen after the data has been mapped to a voter precinct since our objective is to determine the demographics of a voter precinct and not the individual census groups

In [219]:
precinct_demo_info = pd.merge(a,m9_total,how='right', left_on='census_tract', right_on='tract' )

In [220]:
precinct_demo_info = precinct_demo_info.drop(['census_tract'],axis=1).sort_values(by='precinct').reset_index(drop=True)

In [221]:
precinct_demo_info.head()

precinct   tract  gender_male  gender_female   total  race_white  \
0  0050001B  910815       2871.0         2401.0  5272.0      3506.0   
1  0050001C  910815       2871.0         2401.0  5272.0      3506.0   
2  0050001D  910815       2871.0         2401.0  5272.0      3506.0   
3  0050001G  910815       2871.0         2401.0  5272.0      3506.0   
4  0050002B  910815       2871.0         2401.0  5272.0      3506.0   

   race_black  race_native_american  race_asian  race_pacific_island  ...  \
0       154.0                   7.0       122.0                  0.0  ...   
1       154.0                   7.0       122.0                  0.0  ...   
2       154.0                   7.0       122.0                  0.0  ...   
3       154.0                   7.0       122.0                  0.0  ...   
4       154.0                   7.0       122.0                  0.0  ...   

   internet_fixed_broadband  internet_dial_up_or_cellular  \
0                    3631.0                         571.0   
1                    3631.0                         571.0   
2                    3631.0                         571.0   
3                    3631.0                         571.0   
4                    3631.0                         571.0   

   internet_no_internet  computer_no_computer  age_18_to_24  age_25_to_34  \
0                 367.0                 410.0         605.0         544.0   
1                 367.0                 410.0         605.0         544.0   
2                 367.0                 410.0         605.0         544.0   
3                 367.0                 410.0         605.0         544.0   
4                 367.0                 410.0         605.0         544.0   

   age_35_to_44  age_45_to_54  age_55_to_64  age_65+  
0         532.0         679.0        1068.0    845.0  
1         532.0         679.0        1068.0    845.0  
2         532.0         679.0        1068.0    845.0  
3         532.0         679.0        1068.0    845.0  
4         532.0         679.0        1068.0    845.0  

[5 rows x 51 columns]

In [222]:
parquet_file = 'precinct_demo_info.parquet'
precinct_demo_info.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

In [223]:
del a, m9_total, precinct_df

##### **2.5 Create Precinct Voter Results File**

Identify the precincts that are included in the voter results info

In [224]:
unique_precincts = voter_selections['precinct'].unique().tolist()

In [225]:
len(unique_precincts)

7661

Create precinct demo table only including those precincts included in the voter responese data

In [226]:
precinct_demo_mini = precinct_demo_info.loc[precinct_demo_info['precinct'].isin(unique_precincts)].sort_values(by='precinct').reset_index(drop=True).copy()

In [227]:
precinct_demo_mini = precinct_demo_mini.drop(['tract'],axis=1)

In [228]:
precinct_demo_mini.head()

precinct  gender_male  gender_female   total  race_white  race_black  \
0  0050001B       2871.0         2401.0  5272.0      3506.0       154.0   
1  0050002B       2871.0         2401.0  5272.0      3506.0       154.0   
2  0050003A       2871.0         2401.0  5272.0      3506.0       154.0   
3  0050004A       2871.0         2401.0  5272.0      3506.0       154.0   
4  0050004B       2871.0         2401.0  5272.0      3506.0       154.0   

   race_native_american  race_asian  race_pacific_island  race_other  ...  \
0                   7.0       122.0                  0.0        12.0  ...   
1                   7.0       122.0                  0.0        12.0  ...   
2                   7.0       122.0                  0.0        12.0  ...   
3                   7.0       122.0                  0.0        12.0  ...   
4                   7.0       122.0                  0.0        12.0  ...   

   internet_fixed_broadband  internet_dial_up_or_cellular  \
0                    3631.0                         571.0   
1                    3631.0                         571.0   
2                    3631.0                         571.0   
3                    3631.0                         571.0   
4                    3631.0                         571.0   

   internet_no_internet  computer_no_computer  age_18_to_24  age_25_to_34  \
0                 367.0                 410.0         605.0         544.0   
1                 367.0                 410.0         605.0         544.0   
2                 367.0                 410.0         605.0         544.0   
3                 367.0                 410.0         605.0         544.0   
4                 367.0                 410.0         605.0         544.0   

   age_35_to_44  age_45_to_54  age_55_to_64  age_65+  
0         532.0         679.0        1068.0    845.0  
1         532.0         679.0        1068.0    845.0  
2         532.0         679.0        1068.0    845.0  
3         532.0         679.0        1068.0    845.0  
4         532.0         679.0        1068.0    845.0  

[5 rows x 50 columns]

In [229]:
parquet_file = 'precinct_demo_info.parquet'
precinct_demo_mini.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

##### **2.6 Master Probability Files for Naive Bayes Classifier**

Create Precinct Demographic Totals

In [230]:
col_prefix = []

for col in precinct_demo_info.columns.unique().tolist():
    if re.search("_",col) != None:
        result = re.split("_",col)[0]
        if result not in col_prefix:
            col_prefix.append(result)


In [231]:
df_cols = precinct_demo_info.columns.unique().tolist()

precinct_df_totals = pd.DataFrame()

for prefix in col_prefix:
    selected_cols = []
    for col in df_cols:
        search_string = '^'+prefix
        if re.search(search_string,col) != None:
            selected_cols.append(col)
    
    selected_cols.insert(0,'precinct')

    temp_df = precinct_demo_mini.loc[:,selected_cols]
    temp_df = temp_df.set_index(['precinct'])
    new_col = prefix+'_total'
    temp_df[new_col] = temp_df.apply(lambda x: x.sum(), axis=1)

    precinct_df_totals = pd.concat([precinct_df_totals,temp_df],axis=1)

In [232]:

precinct_df_totals.head()

gender_male  gender_female  gender_total  race_white  race_black  \
precinct                                                                     
0050001B       2871.0         2401.0        5272.0      3506.0       154.0   
0050002B       2871.0         2401.0        5272.0      3506.0       154.0   
0050003A       2871.0         2401.0        5272.0      3506.0       154.0   
0050004A       2871.0         2401.0        5272.0      3506.0       154.0   
0050004B       2871.0         2401.0        5272.0      3506.0       154.0   

          race_native_american  race_asian  race_pacific_island  race_other  \
precinct                                                                      
0050001B                   7.0       122.0                  0.0        12.0   
0050002B                   7.0       122.0                  0.0        12.0   
0050003A                   7.0       122.0                  0.0        12.0   
0050004A                   7.0       122.0                  0.0        12.0   
0050004B                   7.0       122.0                  0.0        12.0   

          race_two_plus_races  ...  internet_dial_up_or_cellular  \
precinct                       ...                                 
0050001B                 97.0  ...                         571.0   
0050002B                 97.0  ...                         571.0   
0050003A                 97.0  ...                         571.0   
0050004A                 97.0  ...                         571.0   
0050004B                 97.0  ...                         571.0   

          internet_no_internet  internet_total  age_18_to_24  age_25_to_34  \
precinct                                                                     
0050001B                 367.0          4569.0         605.0         544.0   
0050002B                 367.0          4569.0         605.0         544.0   
0050003A                 367.0          4569.0         605.0         544.0   
0050004A                 367.0          4569.0         605.0         544.0   
0050004B                 367.0          4569.0         605.0         544.0   

          age_35_to_44  age_45_to_54  age_55_to_64  age_65+  age_total  
precinct                                                                
0050001B         532.0         679.0        1068.0    845.0     4273.0  
0050002B         532.0         679.0        1068.0    845.0     4273.0  
0050003A         532.0         679.0        1068.0    845.0     4273.0  
0050004A         532.0         679.0        1068.0    845.0     4273.0  
0050004B         532.0         679.0        1068.0    845.0     4273.0  

[5 rows x 59 columns]

Create precinct level demographic percentages by category

In [233]:
df_cols = precinct_df_totals.columns.tolist()

precinct_df_pcts = pd.DataFrame()

for prefix in col_prefix:
    selected_cols = []
    for col in df_cols:
        search_string = '^'+prefix
        if re.search(search_string,col) != None:
            selected_cols.append(col)

    
    
    temp_df = precinct_df_totals.loc[:,selected_cols]
    temp_df = temp_df.apply(lambda x: x/x[selected_cols[-1]],axis=1)
        
    
    #temp_df[new_col] = temp_df.apply(lambda x: x.sum(), axis=1)

    precinct_df_pcts = pd.concat([precinct_df_pcts,temp_df],axis=1)

In [234]:
precinct_df_pcts.head()

gender_male  gender_female  gender_total  race_white  race_black  \
precinct                                                                     
0050001B     0.544575       0.455425           1.0    0.665023    0.029211   
0050002B     0.544575       0.455425           1.0    0.665023    0.029211   
0050003A     0.544575       0.455425           1.0    0.665023    0.029211   
0050004A     0.544575       0.455425           1.0    0.665023    0.029211   
0050004B     0.544575       0.455425           1.0    0.665023    0.029211   

          race_native_american  race_asian  race_pacific_island  race_other  \
precinct                                                                      
0050001B              0.001328    0.023141                  0.0    0.002276   
0050002B              0.001328    0.023141                  0.0    0.002276   
0050003A              0.001328    0.023141                  0.0    0.002276   
0050004A              0.001328    0.023141                  0.0    0.002276   
0050004B              0.001328    0.023141                  0.0    0.002276   

          race_two_plus_races  ...  internet_dial_up_or_cellular  \
precinct                       ...                                 
0050001B             0.018399  ...                      0.124973   
0050002B             0.018399  ...                      0.124973   
0050003A             0.018399  ...                      0.124973   
0050004A             0.018399  ...                      0.124973   
0050004B             0.018399  ...                      0.124973   

          internet_no_internet  internet_total  age_18_to_24  age_25_to_34  \
precinct                                                                     
0050001B              0.080324             1.0      0.141587      0.127311   
0050002B              0.080324             1.0      0.141587      0.127311   
0050003A              0.080324             1.0      0.141587      0.127311   
0050004A              0.080324             1.0      0.141587      0.127311   
0050004B              0.080324             1.0      0.141587      0.127311   

          age_35_to_44  age_45_to_54  age_55_to_64   age_65+  age_total  
precinct                                                                 
0050001B      0.124503      0.158905      0.249941  0.197753        1.0  
0050002B      0.124503      0.158905      0.249941  0.197753        1.0  
0050003A      0.124503      0.158905      0.249941  0.197753        1.0  
0050004A      0.124503      0.158905      0.249941  0.197753        1.0  
0050004B      0.124503      0.158905      0.249941  0.197753        1.0  

[5 rows x 59 columns]

In [235]:
remove_cols = [col for col in precinct_df_pcts.columns.tolist() if re.search('total',col) != None ]

In [236]:
precinct_df_pcts = precinct_df_pcts.drop(remove_cols,axis=1).reset_index()

In [237]:
precinct_df_pcts.head()

precinct  gender_male  gender_female  race_white  race_black  \
0  0050001B     0.544575       0.455425    0.665023    0.029211   
1  0050002B     0.544575       0.455425    0.665023    0.029211   
2  0050003A     0.544575       0.455425    0.665023    0.029211   
3  0050004A     0.544575       0.455425    0.665023    0.029211   
4  0050004B     0.544575       0.455425    0.665023    0.029211   

   race_native_american  race_asian  race_pacific_island  race_other  \
0              0.001328    0.023141                  0.0    0.002276   
1              0.001328    0.023141                  0.0    0.002276   
2              0.001328    0.023141                  0.0    0.002276   
3              0.001328    0.023141                  0.0    0.002276   
4              0.001328    0.023141                  0.0    0.002276   

   race_two_plus_races  ...  computer_no_computer  internet_fixed_broadband  \
0             0.018399  ...              0.082346                  0.794703   
1             0.018399  ...              0.082346                  0.794703   
2             0.018399  ...              0.082346                  0.794703   
3             0.018399  ...              0.082346                  0.794703   
4             0.018399  ...              0.082346                  0.794703   

   internet_dial_up_or_cellular  internet_no_internet  age_18_to_24  \
0                      0.124973              0.080324      0.141587   
1                      0.124973              0.080324      0.141587   
2                      0.124973              0.080324      0.141587   
3                      0.124973              0.080324      0.141587   
4                      0.124973              0.080324      0.141587   

   age_25_to_34  age_35_to_44  age_45_to_54  age_55_to_64   age_65+  
0      0.127311      0.124503      0.158905      0.249941  0.197753  
1      0.127311      0.124503      0.158905      0.249941  0.197753  
2      0.127311      0.124503      0.158905      0.249941  0.197753  
3      0.127311      0.124503      0.158905      0.249941  0.197753  
4      0.127311      0.124503      0.158905      0.249941  0.197753  

[5 rows x 49 columns]

Create Population Category Totals by Precinct

In [238]:
precinct_pct_total = pd.DataFrame((precinct_df_totals['gender_total']/precinct_df_totals['gender_total'].sum())*100)

In [239]:
precinct_pct_total = precinct_pct_total.rename(columns={'gender_total':'pct_total'})

In [240]:
precinct_pct_total = precinct_pct_total.reset_index()

In [241]:
precinct_pct_total.head()

precinct  pct_total
0  0050001B   0.009386
1  0050002B   0.009386
2  0050003A   0.009386
3  0050004A   0.009386
4  0050004B   0.009386

Create category probabilities 

In [242]:
pd.DataFrame(precinct_df_totals.sum()).T

gender_male  gender_female  gender_total  race_white  race_black  \
0   27804967.0     28365274.0    56170241.0  15331937.0   4223573.0   

   race_native_american  race_asian  race_pacific_island  race_other  \
0              113110.0   8523929.0             128185.0    287931.0   

   race_two_plus_races  ...  internet_dial_up_or_cellular  \
0            1811124.0  ...                     5759405.0   

   internet_no_internet  internet_total  age_18_to_24  age_25_to_34  \
0             2511034.0      53558448.0     5136009.0     8563262.0   

   age_35_to_44  age_45_to_54  age_55_to_64    age_65+   age_total  
0     7750098.0     7558842.0     7054515.0  7507098.0  43569824.0  

[1 rows x 59 columns]

In [243]:
df_cols = pd.DataFrame(precinct_df_totals.sum()).T.columns.tolist()

category_pcts_df = pd.DataFrame()

for prefix in col_prefix:
    selected_cols = []
    for col in df_cols:
        search_string = '^'+prefix
        if re.search(search_string,col) != None:
            selected_cols.append(col)

    
    
    temp_df = pd.DataFrame(precinct_df_totals.sum()).T.loc[:,selected_cols]
    temp_df = temp_df.apply(lambda x: x/x[selected_cols[-1]],axis=1)
        
    
    #temp_df[new_col] = temp_df.apply(lambda x: x.sum(), axis=1)

    category_pcts_df = pd.concat([category_pcts_df,temp_df],axis=1)

In [244]:
remove_cols = [col for col in df_cols if re.search('total',col) != None ]

In [245]:
category_pcts_df = category_pcts_df.drop(remove_cols,axis=1)

In [246]:
category_pcts_df = category_pcts_df.T.rename(columns={0:'category_pct'})

In [247]:
category_pcts_df = category_pcts_df.reset_index()

In [248]:
category_pcts_df.head()

index  category_pct
0           gender_male      0.495012
1         gender_female      0.504988
2            race_white      0.272955
3            race_black      0.075192
4  race_native_american      0.002014

Remove the totals columns from precinct df totals

In [249]:
remove_cols = [col for col in precinct_df_totals.columns.tolist() if re.search('total',col) != None ]

In [250]:
precinct_df_totals = precinct_df_totals.drop(remove_cols,axis=1).reset_index()

In [251]:
precinct_df_totals.head()

precinct  gender_male  gender_female  race_white  race_black  \
0  0050001B       2871.0         2401.0      3506.0       154.0   
1  0050002B       2871.0         2401.0      3506.0       154.0   
2  0050003A       2871.0         2401.0      3506.0       154.0   
3  0050004A       2871.0         2401.0      3506.0       154.0   
4  0050004B       2871.0         2401.0      3506.0       154.0   

   race_native_american  race_asian  race_pacific_island  race_other  \
0                   7.0       122.0                  0.0        12.0   
1                   7.0       122.0                  0.0        12.0   
2                   7.0       122.0                  0.0        12.0   
3                   7.0       122.0                  0.0        12.0   
4                   7.0       122.0                  0.0        12.0   

   race_two_plus_races  ...  computer_no_computer  internet_fixed_broadband  \
0                 97.0  ...                 410.0                    3631.0   
1                 97.0  ...                 410.0                    3631.0   
2                 97.0  ...                 410.0                    3631.0   
3                 97.0  ...                 410.0                    3631.0   
4                 97.0  ...                 410.0                    3631.0   

   internet_dial_up_or_cellular  internet_no_internet  age_18_to_24  \
0                         571.0                 367.0         605.0   
1                         571.0                 367.0         605.0   
2                         571.0                 367.0         605.0   
3                         571.0                 367.0         605.0   
4                         571.0                 367.0         605.0   

   age_25_to_34  age_35_to_44  age_45_to_54  age_55_to_64  age_65+  
0         544.0         532.0         679.0        1068.0    845.0  
1         544.0         532.0         679.0        1068.0    845.0  
2         544.0         532.0         679.0        1068.0    845.0  
3         544.0         532.0         679.0        1068.0    845.0  
4         544.0         532.0         679.0        1068.0    845.0  

[5 rows x 49 columns]

In [252]:
#Update files to S3

parquet_file = 'precinct_demographic_totals.parquet'
precinct_df_totals.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)


parquet_file = 'precinct_demographic_percentages.parquet'
precinct_df_pcts.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)


parquet_file = 'precinct_percent_total.parquet'
precinct_pct_total.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)


parquet_file = 'demographic_percentages.parquet'
category_pcts_df.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

In [253]:
del category_pcts_df, precinct_pct_total, precinct_df_totals, precinct_demo_mini, precinct_demo_info

##### **2.7 Final Features Data**

Setup Text Vectorizers

In [254]:

def clean_string(raw_string):
    new_string = re.sub('A YES vote on this measure means:',"",raw_string)   
    new_string = re.sub('[^\w\s]',"", new_string.lower())
    new_string = re.sub('[\d]',"", new_string)
    new_string = re.sub('[\s]{2,}'," ", new_string)
    tokenized_words = new_string.split(" ")
    results = filter(lambda x: x not in stop_words,tokenized_words)
    cleaned_words = [wordnet_lemmatizer.lemmatize(s) for s in results]
    #print(cleaned_words)
    new_string = " ".join(cleaned_words)
    new_string = new_string.strip()
    return new_string


In [255]:
temp_file = 'tempfile.parquet'


response = s3.list_objects(Bucket= my_bucket,Prefix='clean_files/combined_df_final')

files = response.get("Contents")

s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=files[0]['Key'])
combined_df_final = pd.read_parquet(temp_file)

In [256]:
cp_mini = combined_df_final[['prop_summary', 'doc_name']].copy()


In [257]:
del combined_df_final

In [258]:

samp_text = cp_mini['prop_summary'].tolist()

In [259]:
clean_text = [clean_string(text) for text in samp_text]

In [260]:
count_vectorizer = CountVectorizer()
tf_vectorizer = TfidfTransformer(use_idf=False)

In [261]:
count_vectorizer.fit(clean_text)
X1 = count_vectorizer.transform(clean_text)

tf_vectorizer.fit(X1)
X2 = tf_vectorizer.transform(X1)

In [262]:
dump(count_vectorizer,'count_vectorizer.joblib')
dump(tf_vectorizer,'tf_vectorizer.joblib')

['tf_vectorizer.joblib']

In [263]:
joblib_file = 'count_vectorizer.joblib'
s3.upload_file(Filename=joblib_file,Bucket=my_bucket,Key='clean_files/models/'+joblib_file)

joblib_file = 'tf_vectorizer.joblib'
s3.upload_file(Filename=joblib_file,Bucket=my_bucket,Key='clean_files/models/'+joblib_file)

In [264]:
corpus_features = pd.DataFrame(X2.toarray(),columns=count_vectorizer.get_feature_names_out())


In [265]:
text_features = pd.concat([cp_mini['doc_name'],corpus_features],axis=1)


In [266]:
text_features.head()

doc_name  ability  able  abolishing  abortion  absent  abuse  abuser  \
0  PROP01_2024      0.0   0.0         0.0  0.000000     0.0    0.0     0.0   
1  PROP01_2022      0.0   0.0         0.0  0.235702     0.0    0.0     0.0   
2  PROP26_2022      0.0   0.0         0.0  0.000000     0.0    0.0     0.0   
3  PROP27_2022      0.0   0.0         0.0  0.000000     0.0    0.0     0.0   
4  PROP28_2022      0.0   0.0         0.0  0.000000     0.0    0.0     0.0   

   academic  acceleration  ...  yearolds  yearround  yes  yet  young  youth  \
0       0.0           0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
1       0.0           0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
2       0.0           0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
3       0.0           0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
4       0.0           0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   

   zeroemission  zev  zevs  zone  
0           0.0  0.0   0.0   0.0  
1           0.0  0.0   0.0   0.0  
2           0.0  0.0   0.0   0.0  
3           0.0  0.0   0.0   0.0  
4           0.0  0.0   0.0   0.0  

[5 rows x 1678 columns]

In [267]:
unique_props = voter_selections.prop_code.unique().tolist()


In [268]:
text_features_clean = text_features.loc[text_features['doc_name'].isin(unique_props)].copy()

In [269]:
text_features_clean.head()

doc_name  ability  able  abolishing  abortion  absent  abuse  abuser  \
0  PROP01_2024      0.0   0.0         0.0  0.000000     0.0    0.0     0.0   
1  PROP01_2022      0.0   0.0         0.0  0.235702     0.0    0.0     0.0   
2  PROP26_2022      0.0   0.0         0.0  0.000000     0.0    0.0     0.0   
3  PROP27_2022      0.0   0.0         0.0  0.000000     0.0    0.0     0.0   
4  PROP28_2022      0.0   0.0         0.0  0.000000     0.0    0.0     0.0   

   academic  acceleration  ...  yearolds  yearround  yes  yet  young  youth  \
0       0.0           0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
1       0.0           0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
2       0.0           0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
3       0.0           0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
4       0.0           0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   

   zeroemission  zev  zevs  zone  
0           0.0  0.0   0.0   0.0  
1           0.0  0.0   0.0   0.0  
2           0.0  0.0   0.0   0.0  
3           0.0  0.0   0.0   0.0  
4           0.0  0.0   0.0   0.0  

[5 rows x 1678 columns]

In [270]:
parquet_file = 'text_features.parquet'
text_features_clean.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')

Clear unnecessary variables before creating training data

In [272]:
del available_codes,cp_mini, samp_text

In [273]:
del text_features

In [274]:
m1 = pd.merge(voter_selections, text_features_clean, how='left', left_on='prop_code', right_on='doc_name')

In [275]:
m1.head()

precinct    prop_code voter_choice     doc_name  ability  able  abolishing  \
0  0050003A  PROP10_2018      opposed  PROP10_2018      0.0   0.0         0.0   
1  0050003A  PROP10_2018      opposed  PROP10_2018      0.0   0.0         0.0   
2  0050003A  PROP10_2018      opposed  PROP10_2018      0.0   0.0         0.0   
3  0050003A  PROP10_2018      opposed  PROP10_2018      0.0   0.0         0.0   
4  0050004B  PROP10_2018      opposed  PROP10_2018      0.0   0.0         0.0   

   abortion  absent  abuse  ...  yearolds  yearround  yes  yet  young  youth  \
0       0.0     0.0    0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
1       0.0     0.0    0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
2       0.0     0.0    0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
3       0.0     0.0    0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   
4       0.0     0.0    0.0  ...       0.0        0.0  0.0  0.0    0.0    0.0   

   zeroemission  zev  zevs  zone  
0           0.0  0.0   0.0   0.0  
1           0.0  0.0   0.0   0.0  
2           0.0  0.0   0.0   0.0  
3           0.0  0.0   0.0   0.0  
4           0.0  0.0   0.0   0.0  

[5 rows x 1681 columns]

In [276]:
m2 = pd.merge(m1,precinct_df_pcts,how='left',left_on='precinct', right_on='precinct')

In [277]:
del m1, voter_selections

In [278]:
del text_features_clean

In [ ]:
del results_df

In [ ]:
del precinct_df, precinct_df_pcts, m9_total

In [ ]:
m2.shape

(1513891, 1729)

In [ ]:
parquet_file = 'model_training_data.parquet'
m2.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

In [ ]:
del results, row_data, rows,

In [ ]:
m2 = m2.dropna()

In [ ]:
parquet_file = 'model_training_data.parquet'
m2.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

#### 3. Model Training and Evaluation

##### 3.1 Setup Precinct Classification Model

**Model 1 - Precinct Similarity Model**

This model will take in the individual features of a voter across several demographic categories, and then determine the precincts that the voter is most likely similar to. 

Key Steps:

- Create a dataframe that is based on the totals for each of the programs 
- Collect aggregate marginal probabilities for the entire dataset  
    - P(Precinct) - based on total population for the precinct vs. overall total
    - And then do the same for each of the sub features that are used in the dataset

This data will be used in the Naive Bayes algorithm to represent P(B) and P(A): P(B|A) = P(A|B)P(B) / P(A)

The conditional probabilities will be based on the data that is in the existing precinct demographic dataset



In [380]:
def get_feature_prob(feature):
    prob_feature = marginal_demo_pcts_df[marginal_demo_pcts_df['index'] == feature]['category_pct'].values[0]
    return prob_feature

In [381]:
def get_cond_feature_prob(feature, precinct):
    cond_prob_feature = precinct_demo_pct_df[precinct_demo_pct_df['precinct'] == precinct][feature].values[0]
    return cond_prob_feature


In [382]:
def get_precinct_prob(precinct):
    prob_precinct = precinct_pct_df[precinct_pct_df['precinct'] == precinct]['pct_total'].values[0]
    return prob_precinct

In [383]:
def calculate_naive_bayes_prob(features_list, precinct):

    features_prob = [get_feature_prob(feature) for feature in features_list]
    #print(features_prob)
    cond_features_prob = [get_cond_feature_prob(feature,precinct) for feature in features_list]
    prob_precinct = get_precinct_prob(precinct)
    #print(prob_precinct)
    #print(cond_features_prob)
    
    #print(np.prod(cond_features_prob)*100)
    #print(np.prod(features_prob)*100)

    nb_prob = (((np.prod(cond_features_prob))*((prob_precinct)))/(np.prod(features_prob)))
    #print(nb_prob)
    return nb_prob

In [384]:
def get_similar_precincts(features_list, num_precincts, precinct_list):
    precinct_probs = [{'precinct':precinct, 'nb_prob':calculate_naive_bayes_prob(features_list,precinct)} for precinct in precinct_list]
    precinct_scores = pd.DataFrame(precinct_probs).sort_values(by='nb_prob', ascending=False)
    precinct_scores = precinct_scores.iloc[:num_precincts].reset_index(drop=True)
    return precinct_scores

##### 3.2 Setup Test and Training Data

In [285]:

temp_file = 'tempfile.parquet'


response = s3.list_objects(Bucket= my_bucket,Prefix='clean_files/model_training_data')

files = response.get("Contents")

s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=files[0]['Key'])
m2 = pd.read_parquet(temp_file)


In [286]:
training_mini = m2.sample(frac=.45).reset_index(drop=True)
training_mini.shape

X = training_mini.iloc[:,4:]
y = training_mini['voter_choice']
y = pd.DataFrame(y).apply(lambda x: 0 if x['voter_choice'] == 'opposed' else 1, axis=1)

In [287]:
X_train,X_test, y_train, y_test = train_test_split(X,y,test_size=0.3, random_state=1211)

In [288]:
del X, m2,y

##### 3.3 Train Models

Naive Bayes Classifier

In [289]:
nb_clf = CategoricalNB()
nb_clf.fit(X_train, y_train)
nb_clf.score(X_test,y_test)

0.5373865887996663

In [290]:
dump(nb_clf,'nb_classifier.joblib')

['nb_classifier.joblib']

Nearest Neighbors Classifier

In [291]:
knn_clf = KNeighborsClassifier(n_neighbors=7)
knn_clf.fit(X_train, y_train)
score = knn_clf.score(X_test,y_test)
print(score)

0.8933599511344844


In [292]:
dump(knn_clf,'knn_classifier.joblib')

['knn_classifier.joblib']

In [293]:
#knn_clf = load('../knn_classifier.joblib')

Logistic Regression Classifier

In [294]:
lr_clf = Pipeline([('scaler',StandardScaler()),('clf',LogisticRegression(max_iter=10000,random_state=1211,solver='saga'))])
lr_clf.fit(X_train, y_train)
lr_clf.score(X_test, y_test)

0.8734015662788215

In [295]:
dump(lr_clf,'lr_classifier.joblib')

['lr_classifier.joblib']

Random Forrest

In [296]:
rf_clf = RandomForestClassifier(bootstrap=True, random_state=1211)
rf_clf.fit(X_train, y_train)
rf_clf.score(X_test,y_test)

0.8998703871996186

In [297]:
dump(rf_clf,'rf_classifier.joblib')

['rf_classifier.joblib']

Ada Boost

In [298]:
ab_clf = AdaBoostClassifier()
ab_clf.fit(X_train, y_train)
ab_clf.score(X_test, y_test)

0.8513375941679205

In [299]:
dump(ab_clf,'ab_classifier.joblib')

['ab_classifier.joblib']

Bagging

In [300]:
bag_clf = BaggingClassifier()
bag_clf.fit(X_train, y_train)
bag_clf.score(X_test, y_test)

0.9015637958176284

In [301]:
dump(bag_clf,'bag_classifier.joblib')

['bag_classifier.joblib']

Neural Network

In [302]:
nnet_clf = MLPClassifier()
nnet_clf.fit(X_train, y_train)
nnet_clf.score(X_test, y_test)

0.9077315773530186

In [303]:

dump(nnet_clf,'nnet_classifier.joblib')


['nnet_classifier.joblib']

In [304]:


joblib_file = 'nb_classifier.joblib'
s3.upload_file(Filename=joblib_file,Bucket=my_bucket,Key='clean_files/models/'+joblib_file)

joblib_file = 'knn_classifier.joblib'
s3.upload_file(Filename=joblib_file,Bucket=my_bucket,Key='clean_files/models/'+joblib_file)

joblib_file = 'lr_classifier.joblib'
s3.upload_file(Filename=joblib_file,Bucket=my_bucket,Key='clean_files/models/'+joblib_file)

joblib_file = 'rf_classifier.joblib'
s3.upload_file(Filename=joblib_file,Bucket=my_bucket,Key='clean_files/models/'+joblib_file)

joblib_file = 'ab_classifier.joblib'
s3.upload_file(Filename=joblib_file,Bucket=my_bucket,Key='clean_files/models/'+joblib_file)

joblib_file = 'bag_classifier.joblib'
s3.upload_file(Filename=joblib_file,Bucket=my_bucket,Key='clean_files/models/'+joblib_file)

joblib_file = 'nnet_classifier.joblib'
s3.upload_file(Filename=joblib_file,Bucket=my_bucket,Key='clean_files/models/'+joblib_file)



In [305]:
parquet_file = 'model_training_data_mini.parquet'
training_mini.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

In [ ]:
del X_train, X_test, y_test, y_train

#### 4. User Data Pre-processing

**Import Evaluation Data**

Import and clean the imported user response data

In [308]:
def map_response(value):
    standard_response = response_mapping_mini[response_mapping_mini['Response'] == value]['standard_response'].values[0]
    return standard_response

Algorithm used to make the final prediction for the user level data based on the combination of different predictions made based on precinct similarity

In [320]:
def calculate_prediction(calc_method, pred_df):
    temp_df = pred_df.copy()
    
    #print(temp_df)

    if calc_method == 'majority':
        num_precincts = len(temp_df[temp_df['precinct_score'] > 0])
        predictions_sum = temp_df[temp_df['precinct_score'] > 0]['prediction'].sum()
        #print('predictions_sum: {}, num_precincts: {}'.format(predictions_sum,num_precincts)
        if predictions_sum/num_precincts > .5: 
            prediction = 'Support'
        else: 
            prediction = 'Oppose'
        #print('predictions_sum: {}, num_precincts: {}, prediction: {}'.format(predictions_sum,num_precincts,prediction)
    elif calc_method == 'weighted':
        temp_df['weighted_score'] = temp_df['precinct_score']/temp_df['precinct_score'].sum()
        if sum(temp_df['prediction']*temp_df['weighted_score']) > .5: 
            prediction = 'Support'
        else: 
            prediction = 'Oppose'
        #print('prediction: {}'.format(prediction)
    return prediction

In [309]:
response = s3.list_objects(Bucket= my_bucket, Prefix="clean_files/user_responses")
files = response.get("Contents")

In [310]:
temp_file = 'tempfile.csv'
key = files[0]['Key']
s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=key)
    
user_responses_raw = pd.read_csv(temp_file)

In [311]:
response = s3.list_objects(Bucket= my_bucket, Prefix="clean_files/response_mapping")
files = response.get("Contents")

temp_file = 'tempfile.csv'
key = files[0]['Key']
s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=key)
    
response_mapping = pd.read_csv(temp_file)

In [312]:
user_responses_raw = user_responses_raw.assign(user_id=range(len(user_responses_raw)))
user_responses_melt = pd.melt(user_responses_raw, id_vars=user_responses_raw.columns[[1,2,3,4,5,6,7,8,9,10,11,29]], value_vars=user_responses_raw.columns[12:26])
demographic_info = pd.DataFrame(user_responses_melt.columns).iloc[:11][0].tolist()

col_categories = ['gender', 'race','age','education','marital_status','tenure','computer','internet',\
    'employment','income','health_insurance']

demographic_cols = {}

for i in range(len(demographic_info)):
    demographic_cols[demographic_info[i]] = col_categories[i]
survey_questions = pd.DataFrame(user_responses_raw.columns).iloc[12:26][0].tolist()
question_column_names = {}

for i in range(len(survey_questions)):
    question_column_names[survey_questions[i]] = "question_"+str(i)

user_responses_melt = user_responses_melt.rename(columns=demographic_cols)
response_mapping_mini = response_mapping.loc[:,['standard_response','Response']].copy()
user_responses_melt.iloc[:,:11] = user_responses_melt.iloc[:,:11].map(map_response).copy()



In [313]:
parquet_file = 'user_responses_clean.parquet'
user_responses_melt.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

Evaluate User Responses

In [314]:
unique_statements = user_responses_melt['variable'].unique().tolist()
corpus = [clean_string(raw_text) for raw_text in unique_statements]
X_count = count_vectorizer.transform(corpus)
X_new = tf_vectorizer.transform(X_count)
X_new.toarray()
X_new = pd.DataFrame(X_new.toarray(),columns=count_vectorizer.get_feature_names_out())

unique_precincts = training_mini['precinct'].unique().tolist()

In [434]:
X_new.shape

(14, 1677)

In [436]:
training_mini.shape

(671227, 1729)

In [318]:

clf_list = ['bag_classifier.joblib','rf_classifier.joblib','knn_classifier.joblib',\
    'nnet_classifier.joblib','lr_classifier.joblib']


In [319]:
#Import classifiers if not in memory

temp_file = 'tempfile.joblib'

try:
    bag_clf
except NameError:
    response = s3.list_objects(Bucket= my_bucket, Prefix="clean_files/models/"+clf_list[0])
    files = response.get("Contents")
    key = files[0]['Key']
    s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=key)
    bag_clf = load(temp_file)


try:
    rf_clf
except NameError:
    response = s3.list_objects(Bucket= my_bucket, Prefix="clean_files/models/"+clf_list[1])
    files = response.get("Contents")
    key = files[0]['Key']
    s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=key)
    rf_clf = load(temp_file)


try:
    knn_clf
except NameError:
    response = s3.list_objects(Bucket= my_bucket, Prefix="clean_files/models/"+clf_list[2])
    files = response.get("Contents")
    key = files[0]['Key']
    s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=key)
    knn_clf = load(temp_file)

try:
    nnet_clf
except NameError:
    response = s3.list_objects(Bucket= my_bucket, Prefix="clean_files/models/"+clf_list[3])
    files = response.get("Contents")
    key = files[0]['Key']
    s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=key)
    nnet_clf = load(temp_file)


try:
    lr_clf
except NameError:
    response = s3.list_objects(Bucket= my_bucket, Prefix="clean_files/models/"+clf_list[4])
    files = response.get("Contents")
    key = files[0]['Key']
    s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=key)
    lr_clf = load(temp_file)


Download Precinct Demographic variables if not in memory

In [323]:

temp_file = 'tempfile.parquet'

census_files = ['precinct_demographic_percentages.parquet',\
'precinct_percent_total.parquet','demographic_percentages.parquet']


try:
    precinct_demo_pct_df
except NameError:
    response = s3.list_objects(Bucket= my_bucket, Prefix="clean_files/"+census_files[0])
    files = response.get("Contents")
    key = files[0]['Key']
    s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=key)
    precinct_demo_pct_df = pd.read_parquet(temp_file)

try:
    precinct_pct_df
except NameError:
    response = s3.list_objects(Bucket= my_bucket, Prefix="clean_files/"+census_files[1])
    files = response.get("Contents")
    key = files[0]['Key']
    s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=key)
    precinct_pct_df = pd.read_parquet(temp_file)

try:
    marginal_demo_pcts_df
except NameError:
    response = s3.list_objects(Bucket= my_bucket, Prefix="clean_files/"+census_files[2])
    files = response.get("Contents")
    key = files[0]['Key']
    s3.download_file(Filename=temp_file, Bucket=my_bucket, Key=key)
    marginal_demo_pcts_df = pd.read_parquet(temp_file)

Build Calculated Responses Table

In [353]:
precinct_pct_df

precinct  pct_total
0      0050001B   0.009386
1      0050002B   0.009386
2      0050003A   0.009386
3      0050004A   0.009386
4      0050004B   0.009386
...         ...        ...
13110  9007985F   0.004623
13111  9008147A   0.007621
13112  9008296A   0.005855
13113  9008296A   0.006995
13114  9008296A   0.007419

[13115 rows x 2 columns]

In [385]:
user_responses_list = []
n_precincts = [5,7,9]

classifiers = {'bagging':bag_clf,'random_forest':rf_clf,'knn':knn_clf,'nnet':nnet_clf,'log_reg':lr_clf}
classifier_names = list(classifiers.keys())

calc_methods = ['weighted','majority']



for user_id in user_responses_melt['user_id'].unique().tolist():
    #user_eval_dict = {}
    mini_df = user_responses_melt.loc[user_responses_melt['user_id'] == user_id].reset_index(drop=True).copy()
    user_features = mini_df.iloc[0,0:11].tolist()
    
    similar_precincts_all = get_similar_precincts(user_features,12,unique_precincts)
    
    for num_precincts in n_precincts:
        
        similar_precincts = similar_precincts_all.iloc[:num_precincts]
        #print(similar_precincts)

        for row in range(len(mini_df)):
            
            
            actual_value = mini_df.loc[row,'value']
            
            
            for clf_name in classifier_names:
                classifier = classifiers[clf_name]

                precinct_predictions = []    
                for i in range(len(similar_precincts)):
                    mini_dict = {}
                    precinct = similar_precincts.loc[i,'precinct']
                    precinct_score = similar_precincts.loc[i,'nb_prob']
                    
                    demo_features = precinct_demo_pct_df[precinct_demo_pct_df['precinct'] == precinct]
                    features = pd.DataFrame(demo_features.iloc[:,1:].mean()).T.iloc[0]
                    #features = demo_features.loc[:,~demo_features.columns.isin(['precinct'])].iloc[0]
                    #print(Xn)
                    text_vect = X_new.iloc[row]
                    Xn = pd.concat([pd.DataFrame(text_vect).T.reset_index(drop=True),pd.DataFrame(features).T.reset_index(drop=True)],axis=1)
                
                
                    
                    prediction = classifier.predict(Xn).tolist()[0]
                
                    mini_dict['precinct'] = precinct
                    mini_dict['precinct_score'] = precinct_score
                    mini_dict['prediction'] = prediction
                    precinct_predictions.append(mini_dict)
                    
                    
                
                predictions_df = pd.DataFrame(precinct_predictions)
                #predictions_df['prediction'] = predictions_df['prediction'].apply(lambda x: 1 if x =='Support' else 0)
                #print(predictions_df)

                for calc_type in calc_methods:
                    predicted_value = calculate_prediction(calc_type, predictions_df)

                    user_eval_dict = {}
                    user_eval_dict['user_id'] = user_id
                    user_eval_dict['question_num'] = row
                    user_eval_dict['num_precincts'] = num_precincts
                    user_eval_dict['predicted'] = predicted_value
                    user_eval_dict['actual'] = actual_value
                    user_eval_dict['classifier'] = clf_name
                    user_eval_dict['calc_method'] = calc_type
                    

                    print(user_eval_dict)

                    user_responses_list.append(user_eval_dict)

{'user_id': 0, 'question_num': 0, 'num_precincts': 5, 'predicted': 'Oppose', 'actual': 'Support', 'classifier': 'bagging', 'calc_method': 'weighted'}
{'user_id': 0, 'question_num': 0, 'num_precincts': 5, 'predicted': 'Oppose', 'actual': 'Support', 'classifier': 'bagging', 'calc_method': 'majority'}
{'user_id': 0, 'question_num': 0, 'num_precincts': 5, 'predicted': 'Oppose', 'actual': 'Support', 'classifier': 'random_forest', 'calc_method': 'weighted'}
{'user_id': 0, 'question_num': 0, 'num_precincts': 5, 'predicted': 'Oppose', 'actual': 'Support', 'classifier': 'random_forest', 'calc_method': 'majority'}
{'user_id': 0, 'question_num': 0, 'num_precincts': 5, 'predicted': 'Oppose', 'actual': 'Support', 'classifier': 'knn', 'calc_method': 'weighted'}
{'user_id': 0, 'question_num': 0, 'num_precincts': 5, 'predicted': 'Oppose', 'actual': 'Support', 'classifier': 'knn', 'calc_method': 'majority'}
{'user_id': 0, 'question_num': 0, 'num_precincts': 5, 'predicted': 'Oppose', 'actual': 'Support'

In [386]:
responses_df = pd.DataFrame(user_responses_list)

In [387]:
responses_df.shape

(26880, 7)

In [388]:
parquet_file = 'user_responses_analysis.parquet'
responses_df.to_parquet(parquet_file, engine = 'pyarrow', compression = 'gzip')
s3.upload_file(Filename=parquet_file,Bucket=my_bucket,Key='clean_files/'+parquet_file)

In [ ]:
del precinct_demo_pct_df, precinct_pct_df, marginal_demo_pcts_df

#### **5. User Data Analysis**

##### 5.1 Over Model Performance

In [389]:
precinct_options = responses_df['num_precincts'].unique().tolist()
classifier_options = responses_df['classifier'].unique().tolist()
calc_options = responses_df['calc_method'].unique().tolist()

In [391]:
model_performance = []
question_performance = []

for precinct in precinct_options:
    for classifier in classifier_options:
        for calc in calc_options:
            mini_dict = {}            
            df_mini = responses_df.loc[(responses_df['num_precincts'] == precinct) & (responses_df['classifier'] == classifier) & \
                (responses_df['calc_method'] == calc)].copy()
            
            results_table = pd.crosstab(df_mini['predicted'], df_mini['actual'],margins=True)
            TP = results_table.iloc[1,1]
            TN = results_table.iloc[0,0]
            FP = results_table.iloc[1,0]
            FN = results_table.iloc[0,1]

            accuracy = (TP + TN)/(TP+TN+FP+FN)
            precision = TP / (TP + FP)
            recall = TP / (TP + FN)
            f1_score = ((precision * recall)/(precision + recall))*2

            mini_dict['classifier'] = classifier
            mini_dict['num_precincts'] = precinct
            mini_dict['calc_method'] = calc
            mini_dict['accuracy'] = accuracy
            mini_dict['precision'] = precision
            mini_dict['recall'] = recall
            mini_dict['f1_score'] = f1_score
            model_performance.append(mini_dict)

            df_mini['prediction_result'] = df_mini.apply(lambda x: 1 if x['predicted'] == x['actual'] else 0, axis=1)
            question_results = df_mini.groupby('question_num').agg({'prediction_result':'sum','question_num':len}).reset_index(drop=True)
            for i in range(len(question_results)):
                question_dict = {}
                question_dict['classifier'] = classifier
                question_dict['num_precincts'] = precinct
                question_dict['calc_method'] = calc
                question_dict['question_num'] = i
                question_dict['pct_correct'] = round(question_results.iloc[i,0]/question_results.iloc[i,1],4)
                question_performance.append(question_dict)

            print(mini_dict)

{'classifier': 'bagging', 'num_precincts': 5, 'calc_method': 'weighted', 'accuracy': 0.5412946428571429, 'precision': 0.7724770642201835, 'recall': 0.594632768361582, 'f1_score': 0.6719872306464486}
{'classifier': 'bagging', 'num_precincts': 5, 'calc_method': 'majority', 'accuracy': 0.5412946428571429, 'precision': 0.7724770642201835, 'recall': 0.594632768361582, 'f1_score': 0.6719872306464486}
{'classifier': 'random_forest', 'num_precincts': 5, 'calc_method': 'weighted', 'accuracy': 0.5747767857142857, 'precision': 0.7924865831842576, 'recall': 0.6257062146892656, 'f1_score': 0.6992896606156275}
{'classifier': 'random_forest', 'num_precincts': 5, 'calc_method': 'majority', 'accuracy': 0.5747767857142857, 'precision': 0.7924865831842576, 'recall': 0.6257062146892656, 'f1_score': 0.6992896606156275}
{'classifier': 'knn', 'num_precincts': 5, 'calc_method': 'weighted', 'accuracy': 0.5334821428571429, 'precision': 0.8138528138528138, 'recall': 0.5310734463276836, 'f1_score': 0.642735042735

In [392]:
user_results_df = pd.DataFrame(model_performance).sort_values(by='accuracy', ascending=False)

Accuracy Summary

In [394]:
pd.pivot_table(user_results_df,index=['classifier'],columns=['calc_method','num_precincts'], values='accuracy')

calc_method    majority                      weighted                    
num_precincts         5         7         9         5         7         9
classifier                                                               
bagging        0.541295  0.546875  0.579241  0.541295  0.547991  0.555804
knn            0.534598  0.531250  0.562500  0.533482  0.532366  0.537946
log_reg        0.584821  0.578125  0.581473  0.584821  0.582589  0.580357
nnet           0.537946  0.534598  0.540179  0.536830  0.533482  0.537946
random_forest  0.574777  0.577009  0.591518  0.574777  0.577009  0.582589

In [437]:
pd.pivot_table(user_results_df,index=['classifier'],columns=['calc_method','num_precincts'], values='accuracy').\
    to_csv('user_performance_accuracy.csv')

In [395]:
pd.pivot_table(user_results_df,index=['classifier'], values='accuracy').sort_values(by='accuracy', ascending=False)

accuracy
classifier             
log_reg        0.582031
random_forest  0.579613
bagging        0.552083
knn            0.538690
nnet           0.536830

Precision Summary

In [435]:
pd.pivot_table(user_results_df,index=['classifier'],columns=['calc_method','num_precincts'], values='precision')


calc_method    majority                      weighted                    
num_precincts         5         7         9         5         7         9
classifier                                                               
bagging        0.772477  0.779630  0.785838  0.772477  0.776965  0.778777
knn            0.814255  0.807692  0.813492  0.813853  0.809422  0.806250
log_reg        0.819392  0.817308  0.818356  0.819392  0.818702  0.820463
nnet           0.807531  0.814255  0.809623  0.805846  0.811159  0.811441
random_forest  0.792487  0.794275  0.795848  0.792487  0.795332  0.794014

Overall Summary

In [398]:
pd.pivot_table(user_results_df,index=['classifier'], values=['accuracy','precision','recall','f1_score'])

accuracy  f1_score  precision    recall
classifier                                            
bagging        0.552083  0.681357   0.777694  0.606403
knn            0.538690  0.650162   0.810827  0.542844
log_reg        0.582031  0.695729   0.818935  0.604755
nnet           0.536830  0.648487   0.809976  0.540725
random_forest  0.579613  0.703689   0.794074  0.631827

In [438]:
pd.pivot_table(user_results_df,index=['classifier'], values=['accuracy','precision','recall','f1_score']).\
    to_csv('summary_performance_metrics.csv')

In [399]:
summary_performance = pd.pivot_table(user_results_df,index=['classifier'], values=['accuracy','precision','recall','f1_score'])

In [400]:
accuracy_rank = pd.DataFrame(summary_performance['accuracy']).sort_values(by='accuracy', ascending=False).apply(lambda x: x.rank(ascending=False), axis=0)
precision_rank = pd.DataFrame(summary_performance['precision']).sort_values(by='precision', ascending=False).apply(lambda x: x.rank(ascending=False), axis=0)
recall_rank = pd.DataFrame(summary_performance['recall']).sort_values(by='recall', ascending=False).apply(lambda x: x.rank(ascending=False), axis=0)
f1_rank = pd.DataFrame(summary_performance['f1_score']).sort_values(by='f1_score', ascending=False).apply(lambda x: x.rank(ascending=False), axis=0)

In [402]:
pd.concat([accuracy_rank,precision_rank,recall_rank,f1_rank],axis=1)

accuracy  precision  recall  f1_score
classifier                                          
log_reg             1.0        1.0     3.0       2.0
random_forest       2.0        4.0     1.0       1.0
bagging             3.0        5.0     2.0       3.0
knn                 4.0        2.0     4.0       4.0
nnet                5.0        3.0     5.0       5.0

In [439]:
pd.concat([accuracy_rank,precision_rank,recall_rank,f1_rank],axis=1).to_csv('performance_ranks.csv')

In [403]:
df_mini['prediction_result'] = df_mini.apply(lambda x: 1 if x['predicted'] == x['actual'] else 0, axis=1)

In [404]:
question_df = df_mini.groupby('question_num').agg({'prediction_result':'sum','question_num':len}).reset_index(drop=True)

##### **5.2 Question Analysis**

In [405]:
question_analysis = pd.DataFrame(question_performance)

In [443]:
pd.pivot_table(question_analysis, index='question_num', columns='classifier',
    values='pct_correct', aggfunc=['median'])

median                                        
classifier    bagging      knn log_reg     nnet random_forest
question_num                                                 
0             0.58595  0.40620  0.2031  0.23440       0.24220
1             0.10940  0.29685  0.1094  0.14060       0.20310
2             0.51560  0.43750  0.7188  0.67190       0.72660
3             0.66405  0.65620  0.6719  0.65620       0.67190
4             0.57810  0.72660  0.4219  0.42190       0.53905
5             0.43750  0.40620  0.3594  0.28125       0.50000
6             0.59380  0.64060  0.6250  0.64060       0.59380
7             0.67190  0.50000  0.6562  0.51560       0.61720
8             0.89060  0.89060  0.8906  0.81250       0.85940
9             0.37500  0.43750  0.3750  0.51560       0.37500
10            0.79690  0.78905  0.7812  0.75000       0.78120
11            0.79690  0.42970  0.7969  0.73440       0.79690
12            0.54685  0.50000  0.5625  0.37500       0.68750
13            0.12500  0.39060  0.9844  0.78120       0.53120

In [444]:
pd.pivot_table(question_analysis, index='question_num', columns='classifier',
    values='pct_correct', aggfunc=['median']).to_csv('question_performance.csv')

In [454]:
questions_summary = pd.pivot_table(question_analysis, index='question_num', columns='classifier',
    values='pct_correct', aggfunc=['median']).reset_index()

In [457]:
questions_summary

question_num   median                                        
classifier               bagging      knn log_reg     nnet random_forest
0                     0  0.58595  0.40620  0.2031  0.23440       0.24220
1                     1  0.10940  0.29685  0.1094  0.14060       0.20310
2                     2  0.51560  0.43750  0.7188  0.67190       0.72660
3                     3  0.66405  0.65620  0.6719  0.65620       0.67190
4                     4  0.57810  0.72660  0.4219  0.42190       0.53905
5                     5  0.43750  0.40620  0.3594  0.28125       0.50000
6                     6  0.59380  0.64060  0.6250  0.64060       0.59380
7                     7  0.67190  0.50000  0.6562  0.51560       0.61720
8                     8  0.89060  0.89060  0.8906  0.81250       0.85940
9                     9  0.37500  0.43750  0.3750  0.51560       0.37500
10                   10  0.79690  0.78905  0.7812  0.75000       0.78120
11                   11  0.79690  0.42970  0.7969  0.73440       0.79690
12                   12  0.54685  0.50000  0.5625  0.37500       0.68750
13                   13  0.12500  0.39060  0.9844  0.78120       0.53120

In [462]:
questions_summary['min'] = questions_summary.iloc[:,1:].apply(lambda x: x.min(), axis=1)
questions_summary['max'] = questions_summary.iloc[:,1:].apply(lambda x: x.max(), axis=1)
questions_summary['mean'] = questions_summary.iloc[:,1:].apply(lambda x: x.mean(), axis=1)

In [463]:
questions_summary

question_num   median                                          \
classifier               bagging      knn log_reg     nnet random_forest   
0                     0  0.58595  0.40620  0.2031  0.23440       0.24220   
1                     1  0.10940  0.29685  0.1094  0.14060       0.20310   
2                     2  0.51560  0.43750  0.7188  0.67190       0.72660   
3                     3  0.66405  0.65620  0.6719  0.65620       0.67190   
4                     4  0.57810  0.72660  0.4219  0.42190       0.53905   
5                     5  0.43750  0.40620  0.3594  0.28125       0.50000   
6                     6  0.59380  0.64060  0.6250  0.64060       0.59380   
7                     7  0.67190  0.50000  0.6562  0.51560       0.61720   
8                     8  0.89060  0.89060  0.8906  0.81250       0.85940   
9                     9  0.37500  0.43750  0.3750  0.51560       0.37500   
10                   10  0.79690  0.78905  0.7812  0.75000       0.78120   
11                   11  0.79690  0.42970  0.7969  0.73440       0.79690   
12                   12  0.54685  0.50000  0.5625  0.37500       0.68750   
13                   13  0.12500  0.39060  0.9844  0.78120       0.53120   

                min      max      mean  
classifier                              
0           0.20310  0.58595  0.351557  
1           0.10940  0.29685  0.180800  
2           0.43750  0.72660  0.604929  
3           0.65620  0.67190  0.664050  
4           0.42190  0.72660  0.548007  
5           0.28125  0.50000  0.395086  
6           0.59380  0.64060  0.618314  
7           0.50000  0.67190  0.590400  
8           0.81250  0.89060  0.863829  
9           0.37500  0.51560  0.424100  
10          0.75000  0.79690  0.777893  
11          0.42970  0.79690  0.683057  
12          0.37500  0.68750  0.533479  
13          0.12500  0.98440  0.560257

In [464]:
questions_summary.to_csv('question_model_performance.csv')

##### **5.3 User Level Analysis**

In [412]:

user_performance = []
user_ids = responses_df['user_id'].unique().tolist()

for user in user_ids:
    for precinct in precinct_options:
        for classifier in classifier_options:
            for calc in calc_options:
                mini_dict = {}            
                df_mini = responses_df.loc[(responses_df['user_id'] == user) & (responses_df['num_precincts'] == precinct) &\
                    (responses_df['classifier'] == classifier) & \
                    (responses_df['calc_method'] == calc)].copy()
                
                results_table = pd.crosstab(df_mini['predicted'], df_mini['actual'],margins=True)
                TP = results_table.iloc[1,1]
                TN = results_table.iloc[0,0]
                FP = results_table.iloc[1,0]
                FN = results_table.iloc[0,1]

                accuracy = (TP + TN)/(TP+TN+FP+FN)
                precision = TP / (TP + FP)
                recall = TP / (TP + FN)
                #f1_score = ((precision * recall)/(precision + recall))*2

                mini_dict['user_id'] = user
                mini_dict['classifier'] = classifier
                mini_dict['num_precincts'] = precinct
                mini_dict['calc_method'] = calc
                mini_dict['accuracy'] = accuracy
                mini_dict['precision'] = precision
                mini_dict['recall'] = recall
                #mini_dict['f1_score'] = f1_score
                user_performance.append(mini_dict)
                
                '''
                df_mini['prediction_result'] = df_mini.apply(lambda x: 1 if x['predicted'] == x['actual'] else 0, axis=1)
                question_results = df_mini.groupby('question_num').agg({'prediction_result':'sum','question_num':len}).reset_index(drop=True)
                for i in range(len(question_results)):
                    question_dict = {}
                    question_dict['classifier'] = classifier
                    question_dict['num_precincts'] = precinct
                    question_dict['calc_method'] = calc
                    question_dict['question_num'] = i
                    question_dict['pct_correct'] = round(question_results.iloc[i,0]/question_results.iloc[i,1],4)
                    question_performance.append(question_dict)
                '''
                print(mini_dict)

{'user_id': 0, 'classifier': 'bagging', 'num_precincts': 5, 'calc_method': 'weighted', 'accuracy': 0.2857142857142857, 'precision': 0.75, 'recall': 0.25}
{'user_id': 0, 'classifier': 'bagging', 'num_precincts': 5, 'calc_method': 'majority', 'accuracy': 0.2857142857142857, 'precision': 0.75, 'recall': 0.25}
{'user_id': 0, 'classifier': 'random_forest', 'num_precincts': 5, 'calc_method': 'weighted', 'accuracy': 0.35714285714285715, 'precision': 1.0, 'recall': 0.25}
{'user_id': 0, 'classifier': 'random_forest', 'num_precincts': 5, 'calc_method': 'majority', 'accuracy': 0.35714285714285715, 'precision': 1.0, 'recall': 0.25}
{'user_id': 0, 'classifier': 'knn', 'num_precincts': 5, 'calc_method': 'weighted', 'accuracy': 0.21428571428571427, 'precision': 1.0, 'recall': 0.08333333333333333}
{'user_id': 0, 'classifier': 'knn', 'num_precincts': 5, 'calc_method': 'majority', 'accuracy': 0.21428571428571427, 'precision': 1.0, 'recall': 0.08333333333333333}
{'user_id': 0, 'classifier': 'nnet', 'num_

In [413]:
user_performance_df = pd.DataFrame(user_performance)

In [466]:
pd.pivot_table(user_performance_df, index='user_id', values='accuracy').reset_index()



user_id  accuracy
0         0  0.280952
1         1  0.528571
2         2  0.371429
3         3  0.500000
4         4  0.504762
..      ...       ...
59       59  0.400000
60       60  0.519048
61       61  0.500000
62       62  0.626190
63       63  0.257143

[64 rows x 2 columns]

In [467]:
pd.pivot_table(user_performance_df, index='user_id', values='accuracy').reset_index().\
    to_csv('user_accuracy.csv')



In [416]:
user_responses_raw = user_responses_mea.rename(columns={user_responses_raw.columns[0]:'user_id'})

In [425]:
user_responses_demo = user_responses_melt.iloc[:,1:12].drop_duplicates()

In [468]:
pd.DataFrame(user_responses_demo.columns)

0
0               race
1                age
2          education
3     marital_status
4             tenure
5           computer
6           internet
7         employment
8             income
9   health_insurance
10           user_id

In [469]:
demo_columns = user_responses_demo.columns.tolist()

In [470]:
demo_columns.remove('user_id')

In [427]:
user_performance_demo = pd.merge(user_performance_df,user_responses_demo)

In [ ]:
7-16

In [485]:
user_performance_demo.columns[7:].tolist()

['race',
 'age',
 'education',
 'marital_status',
 'tenure',
 'computer',
 'internet',
 'employment',
 'income',
 'health_insurance']

In [489]:
demographic_details = pd.melt(user_performance_demo, id_vars=user_performance_demo.columns[:7].tolist(),\
    value_vars=user_performance_demo.columns[7:].tolist(),\
        var_name='feature')

Age

In [491]:
demographic_details[demographic_details['feature']=='age'].pivot_table(index='value',columns='classifier', values='accuracy')

classifier     bagging       knn   log_reg      nnet  random_forest
value                                                              
age_18_to_24  0.785714  0.500000  0.857143  0.857143       0.928571
age_25_to_34  0.616497  0.615646  0.596088  0.557823       0.642007
age_35_to_44  0.492369  0.471001  0.526862  0.485653       0.509158
age_45_to_54  0.502976  0.672619  0.571429  0.625000       0.550595
age_55_to_64  0.571429  0.642857  0.785714  0.714286       0.714286
age_65+       0.609524  0.400000  0.554762  0.530952       0.542857

In [505]:
demographic_details[demographic_details['feature']=='age'].\
    pivot_table(index='value',columns='classifier', values='accuracy').\
        to_csv('user_analysis_age.csv')

Race

In [492]:
demographic_details[demographic_details['feature']=='race'].pivot_table(index='value',columns='classifier', values='accuracy')

classifier            bagging       knn   log_reg      nnet  random_forest
value                                                                     
race_asian           0.626984  0.698413  0.595238  0.583333       0.718254
race_black           0.532175  0.501609  0.565315  0.523810       0.552445
race_hispanic        0.452381  0.391156  0.481293  0.421769       0.428571
race_two_plus_races  0.605159  0.654762  0.634921  0.581349       0.678571
race_white           0.534632  0.500000  0.519481  0.536797       0.521645

In [504]:
demographic_details[demographic_details['feature']=='race'].\
    pivot_table(index='value',columns='classifier', values='accuracy').\
        to_csv('user_analysis_race.csv')

Education

In [494]:
demographic_details[demographic_details['feature']=='education'].pivot_table(index='value',columns='classifier', values='accuracy')

classifier                         bagging       knn   log_reg      nnet  \
value                                                                      
education_associates              0.654762  0.535714  0.586310  0.535714   
education_bachelors               0.556437  0.563492  0.567460  0.546296   
education_doctorate               0.473214  0.508929  0.553571  0.547619   
education_hs                      0.166667  0.142857  0.285714  0.119048   
education_masters                 0.512897  0.480159  0.547619  0.519345   
education_professional            0.476190  0.357143  0.428571  0.440476   
education_some_college_no_degree  0.587302  0.468254  0.619048  0.456349   

classifier                        random_forest  
value                                            
education_associates                   0.690476  
education_bachelors                    0.579365  
education_doctorate                    0.508929  
education_hs                           0.190476  
education_masters                      0.525298  
education_professional                 0.357143  
education_some_college_no_degree       0.603175

In [503]:
demographic_details[demographic_details['feature']=='education'].\
    pivot_table(index='value',columns='classifier', values='accuracy').\
        to_csv('user_analysis_education.csv')

Marital Status

In [495]:
demographic_details[demographic_details['feature']=='marital_status'].pivot_table(index='value',columns='classifier', values='accuracy')

classifier                     bagging       knn   log_reg      nnet  \
value                                                                  
marital_status_divorced       0.600340  0.557823  0.600340  0.530612   
marital_status_married        0.468254  0.444004  0.507937  0.471781   
marital_status_never_married  0.593112  0.573980  0.595663  0.572704   
marital_status_widowed        0.398810  0.428571  0.500000  0.494048   

classifier                    random_forest  
value                                        
marital_status_divorced            0.593537  
marital_status_married             0.481481  
marital_status_never_married       0.618622  
marital_status_widowed             0.464286

Tenure

In [496]:
demographic_details[demographic_details['feature']=='tenure'].pivot_table(index='value',columns='classifier', values='accuracy')

classifier          bagging       knn   log_reg      nnet  random_forest
value                                                                   
tenure_home_owner  0.494048  0.432540  0.525132  0.475198       0.503638
tenure_renter      0.588010  0.616071  0.596088  0.584609       0.616922

Computer

In [497]:
demographic_details[demographic_details['feature']=='computer'].pivot_table(index='value',columns='classifier', values='accuracy')

classifier              bagging       knn   log_reg      nnet  random_forest
value                                                                       
computer_has_computer  0.535714  0.511149  0.554800  0.524943       0.553288
computer_no_computer   0.500000  0.619048  0.642857  0.404762       0.547619

Internet

In [499]:
demographic_details[demographic_details['feature']=='internet'].pivot_table(index='value',columns='classifier', values='accuracy')

classifier                     bagging       knn   log_reg      nnet  \
value                                                                  
internet_dial_up_or_cellular  0.595238  0.539683  0.666667  0.587302   
internet_fixed_broadband      0.532201  0.511514  0.550742  0.519906   

classifier                    random_forest  
value                                        
internet_dial_up_or_cellular       0.658730  
internet_fixed_broadband           0.548009

Employment

In [500]:
demographic_details[demographic_details['feature']=='employment'].pivot_table(index='value',columns='classifier', values='accuracy')

classifier                      bagging       knn   log_reg      nnet  \
value                                                                   
employment_employed            0.530284  0.524436  0.552005  0.516917   
employment_not_in_labor_force  0.583333  0.375000  0.550595  0.520833   
employment_unemployed          0.563492  0.476190  0.642857  0.642857   

classifier                     random_forest  
value                                         
employment_employed                 0.549081  
employment_not_in_labor_force       0.535714  
employment_unemployed               0.654762

Income

In [501]:
demographic_details[demographic_details['feature']=='income'].pivot_table(index='value',columns='classifier', values='accuracy')

classifier                 bagging       knn   log_reg      nnet  \
value                                                              
income_between_100k_150k  0.526557  0.507326  0.550366  0.510073   
income_between_150k_200k  0.542659  0.492063  0.548611  0.507937   
income_between_50k_100k   0.558036  0.572173  0.567708  0.566220   
income_less_than_50k      0.591270  0.500000  0.638889  0.593254   
income_over_200k          0.392857  0.392857  0.446429  0.375000   

classifier                random_forest  
value                                    
income_between_100k_150k       0.552198  
income_between_150k_200k       0.537698  
income_between_50k_100k        0.570685  
income_less_than_50k           0.636905  
income_over_200k               0.410714

In [506]:
demographic_details[demographic_details['feature']=='income'].\
    pivot_table(index='value',columns='classifier', values='accuracy').\
        to_csv('user_analysis_income.csv')

Health Insurance

In [502]:
demographic_details[demographic_details['feature']=='health_insurance'].pivot_table(index='value',columns='classifier', values='accuracy')

classifier                        bagging       knn   log_reg      nnet  \
value                                                                     
health_insurance_no_coverage     0.587302  0.507937  0.567460  0.412698   
health_insurance_one_type        0.528669  0.512391  0.539359  0.518707   
health_insurance_two_plus_types  0.548611  0.515873  0.622024  0.568452   

classifier                       random_forest  
value                                           
health_insurance_no_coverage          0.603175  
health_insurance_one_type             0.535957  
health_insurance_two_plus_types       0.611111

In [430]:
user_performance_demo.pivot_table(index='', columns='classifier',values='accuracy')

classifier                 bagging       knn   log_reg      nnet  \
income                                                             
income_between_100k_150k  0.526557  0.507326  0.550366  0.510073   
income_between_150k_200k  0.542659  0.492063  0.548611  0.507937   
income_between_50k_100k   0.558036  0.572173  0.567708  0.566220   
income_less_than_50k      0.591270  0.500000  0.638889  0.593254   
income_over_200k          0.392857  0.392857  0.446429  0.375000   

classifier                random_forest  
income                                   
income_between_100k_150k       0.552198  
income_between_150k_200k       0.537698  
income_between_50k_100k        0.570685  
income_less_than_50k           0.636905  
income_over_200k               0.410714

In [431]:
user_performance_demo.loc[:,['user_id','classifier','accuracy','age']].drop_duplicates().groupby('classifier').agg({'accuracy':['mean','std']})

accuracy          
                   mean       std
classifier                       
bagging        0.529982  0.148918
knn            0.530488  0.184779
log_reg        0.554286  0.119084
nnet           0.511188  0.144366
random_forest  0.544218  0.167020

In [432]:
user_performance_demo.groupby('classifier').agg({'accuracy':['mean','std']})

accuracy          
                   mean       std
classifier                       
bagging        0.535156  0.143600
knn            0.512835  0.182148
log_reg        0.556176  0.119416
nnet           0.523065  0.144155
random_forest  0.553199  0.159050